# Obtain and preprocess data

## Define auxiliary functions

In [ ]:
def compare_real_vs_synthesized_voices(metadata_model_df):

  index = random.choice(metadata_model_df.index)
  reference_audio_id = metadata_model_df.loc[index, 'Reference audio ID']
  reference_audio = os.path.join(reference_audios_path, reference_audio_id +'.wav')
  print('\n Reference audio:')
  IPython.display.display(Audio(reference_audio))

  synthesized_audio_id = metadata_model_df.loc[index, 'Synthesized audio ID']
  synthesized_audio = os.path.join(directory_name, synthesized_audio_id +'.wav')
  print('\n Synthesized speech:')
  IPython.display.display(Audio(synthesized_audio))

In [ ]:
!pip install resemblyzer

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.7/15.7 MB 31.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.2/66.2 kB 4.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 9.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for webrtcvad: filename=webrtcvad-2.0.10-cp310-cp310-linux_x86_64.whl size=73470 sha256=b9f88d43ccf50a2e5ce6608b0dd4bbe264aa56d70ec578ae87a2cc123d0053fe
  Stored in directory: /root/.cache/pip/wheels/2a/2b/84/ac7bacfe8c68a87c1ee3dd3c66818a54c71599abf308e8eb35
  Created wheel for typing: filename=typing-3.7.4.3-py3-none-any.whl size=26304 sha256=c7a2d3fb9dde3713ff141df8767c740c644e795d2db441596dcd9ce2d08f46ef
  Stored in directory: /root/.cache/pip/wheels/7c/d0/9e/1f26ebb66d9e1732e4098bc5a6c2d91f6c9a529838f0284890
Successfully built webrtcvad typing


In [ ]:
import wave
import time
def get_audio_length(file_path):
    with wave.open(file_path, 'rb') as audio_file:
        # Get the number of frames and the frame rate
        num_frames = audio_file.getnframes()
        frame_rate = audio_file.getframerate()

        # Calculate the duration in seconds
        duration = num_frames / frame_rate

    return duration

In [ ]:
import os
import shutil
import glob
import csv
import pandas as pd

def create_dataset(source_directory, destination_directory, min_duration=0, n_speakers=6, n_audios_per_speaker=20, select_speakers_manually=True):

  # Create destination directory if it does not exist
  os.makedirs(destination_directory, exist_ok=True)

  if select_speakers_manually:
    if 'train' in source_directory:
      speakers_id = ['103', '1034', '1040', '1069', '1235', '1088'] # Mujer, hombre, hombre, mujer, hombre, mujer
    else:
      speakers_id = ['1089', '1188', '121', '237', '1284', '1320'] # Hombre, hombre, mujer, mujer, mujer, hombre
  else:
    speakers_id = os.listdir(source_directory)[:n_speakers]

  # Create a DataFrame with audio ID and its transcriptions
  transcriptions_df = pd.DataFrame(columns=['Audio ID', 'Original text', 'Duration', 'Speaker ID'])

  # Fill destination_directory directory with n_audios_per_speaker of more than min_duration (in seconds) and fill transcriptions_df
  for speaker_id in speakers_id:

    speaker_path = os.path.join(source_directory, speaker_id)

    # List n_audios_per_speaker in speaker_path
    wav_files = glob.glob(os.path.join(speaker_path, '**/*.wav'), recursive=True)[:n_audios_per_speaker]

    for wav_file in wav_files:

      duration = get_audio_length(wav_file)

      if duration > min_duration:
        shutil.copy(wav_file, destination_directory)

        audio_id = os.path.splitext(os.path.basename(wav_file))[0]

        directory = os.path.dirname(wav_file)
        text_path = os.path.join(directory, audio_id) + '.original.txt'
        original_text = pd.read_csv(text_path, header=None, quoting=csv.QUOTE_NONE, delimiter='\t').iloc[0,0]

        new_row = pd.DataFrame({'Audio ID':[audio_id],
                                'Original text': [original_text],
                                'Duration': [duration]
                                })

        transcriptions_df = pd.concat([transcriptions_df, new_row])

  n_files = len(os.listdir(destination_directory))
  print(f"{n_files} WAV files copied to " + destination_directory)
  transcriptions_df.reset_index(drop=True, inplace=True)

  # Split the values into separate columns
  df = transcriptions_df['Audio ID'].str.split('_', expand=True)

  # Rename the columns
  df.columns = ['Speaker ID', 'Chapter ID', 'Utterance ID1', 'Utterance ID2']

  # Concatenate 'Utterance_ID2' with 'Utterance_ID1'
  df['Utterance ID'] = df['Utterance ID1'].str.cat(df['Utterance ID2'], sep='_')

  # Drop unnecessary columns
  df = df.drop(columns=['Utterance ID1', 'Utterance ID2'])

  transcriptions_df[['Speaker ID', 'Chapter ID', 'Utterance ID']] = df

  transcriptions_df.to_csv(destination_directory + '_metadata.csv', index=False)

## Obtain training audios

All models use [LibriTTS](https://openslr.org/60/) to train

In [ ]:
# Download training data
!wget https://www.openslr.org/resources/60/train-clean-100.tar.gz

# Extract files
!tar -xf train-clean-100.tar.gz

--2024-01-31 07:14:11--  https://www.openslr.org/resources/60/train-clean-100.tar.gz
Resolving www.openslr.org (www.openslr.org)... 46.101.158.64
Connecting to www.openslr.org (www.openslr.org)|46.101.158.64|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: http://us.openslr.org/resources/60/train-clean-100.tar.gz [following]
--2024-01-31 07:14:12--  http://us.openslr.org/resources/60/train-clean-100.tar.gz
Resolving us.openslr.org (us.openslr.org)... 46.101.158.64
Connecting to us.openslr.org (us.openslr.org)|46.101.158.64|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 7723686890 (7.2G) [application/x-gzip]
Saving to: ‘train-clean-100.tar.gz’

train-clean-100.tar 100%[===================>]   7.19G  24.1MB/s    in 5m 32s  

2024-01-31 07:19:44 (22.2 MB/s) - ‘train-clean-100.tar.gz’ saved [7723686890/7723686890]



In [ ]:
# shutil.rmtree('audio/train')

In [ ]:
destination_directory = 'audio/train'
create_dataset(source_directory='LibriTTS/train-clean-100', destination_directory=destination_directory, min_duration=0)

120 WAV files copied to audio/train


In [ ]:
metadata_train_df = pd.read_csv(destination_directory + '_metadata.csv')
metadata_train_df

Audio ID  \
0       103_1241_000044_000004   
1       103_1241_000066_000006   
2       103_1241_000061_000001   
3       103_1241_000056_000000   
4       103_1241_000052_000006   
..                         ...   
115  1088_134318_000031_000004   
116  1088_134318_000008_000002   
117  1088_134318_000046_000000   
118  1088_134318_000027_000001   
119  1088_134318_000012_000000   

                                         Original text   Duration  Speaker ID  \
0                                   Oh, Mr. Cuthbert!!   1.390000         103   
1    Because, you see, if the bridge DID crumple up...   4.170042         103   
2               Orchard Slope's the name of his place.   1.949958         103   
3                 "That's Barry's pond," said Matthew.   2.150042         103   
4    Did you ever have an ache like that, Mr. Cuthb...   2.410000         103   
..                                                 ...        ...         ...   
115  Gathercole," and Kara came forward with a smil...  11.050000        1088   
116         Ask him if he minds seeing me in my room."   2.110000        1088   
117  He stamped down the stairs as though testing t...   8.740000        1088   
118                            "Pull one out and see!"   1.350000        1088   
119  "By the way, Fisher, after Mr. Gathercole has ...   3.870000        1088   

     Chapter ID   Utterance ID  
0          1241  000044_000004  
1          1241  000066_000006  
2          1241  000061_000001  
3          1241  000056_000000  
4          1241  000052_000006  
..          ...            ...  
115      134318  000031_000004  
116      134318  000008_000002  
117      134318  000046_000000  
118      134318  000027_000001  
119      134318  000012_000000  

[120 rows x 6 columns]

### Reproduce a random audio of the train dataset

In [ ]:
import IPython
from IPython.display import Audio
import random

directory_path = 'audio/train/*.wav'

# Use glob to get a list of wav files
wav_files = glob.glob(directory_path)
wav_files

audio = random.choice(wav_files)
print(audio)
print(metadata_train_df[metadata_train_df['Audio ID'] == os.path.splitext(os.path.basename(audio))[0]].iloc[0,1])
Audio(audio)

audio/train/1235_135884_000001_000000.wav
The Story of the First Old Man and the Hind.


## Obtain test audios

In [ ]:
# Download test data
!wget https://www.openslr.org/resources/60/test-clean.tar.gz

# Extract files
!tar -xf test-clean.tar.gz

--2024-01-31 07:22:10--  https://www.openslr.org/resources/60/test-clean.tar.gz
Resolving www.openslr.org (www.openslr.org)... 46.101.158.64
Connecting to www.openslr.org (www.openslr.org)|46.101.158.64|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: http://us.openslr.org/resources/60/test-clean.tar.gz [following]
--2024-01-31 07:22:11--  http://us.openslr.org/resources/60/test-clean.tar.gz
Resolving us.openslr.org (us.openslr.org)... 46.101.158.64
Connecting to us.openslr.org (us.openslr.org)|46.101.158.64|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1230670113 (1.1G) [application/x-gzip]
Saving to: ‘test-clean.tar.gz’

test-clean.tar.gz   100%[===================>]   1.15G  25.1MB/s    in 48s     

2024-01-31 07:22:59 (24.4 MB/s) - ‘test-clean.tar.gz’ saved [1230670113/1230670113]



In [ ]:
# shutil.rmtree('audio/test')

In [ ]:
destination_directory = 'audio/test'
create_dataset(source_directory='LibriTTS/test-clean', destination_directory=destination_directory, min_duration=0)

120 WAV files copied to audio/test


In [ ]:
metadata_test_df = pd.read_csv(destination_directory + '_metadata.csv')
metadata_test_df

Audio ID  \
0    1089_134691_000025_000003   
1    1089_134691_000053_000002   
2    1089_134691_000044_000001   
3    1089_134691_000027_000004   
4    1089_134691_000010_000002   
..                         ...   
115  1320_122612_000002_000000   
116  1320_122612_000033_000001   
117  1320_122612_000001_000000   
118  1320_122612_000009_000004   
119  1320_122612_000035_000003   

                                         Original text   Duration  Speaker ID  \
0    But he, apart from them and in silence, rememb...   7.000000        1089   
1    His soul was swooning into some new world, fan...   9.419917        1089   
2    He was unheeded, happy and near to the wild he...   4.870000        1089   
3    Now, at the name of the fabulous artificer, he...  11.399958        1089   
4    Idle and embittering, finally, to argue, again...  15.390000        1089   
..                                                 ...        ...         ...   
115  "If you find a man there, he shall die a flea'...   5.850000        1320   
116  This is my schooling, major; and if one neglec...   7.010042        1320   
117                                         CHAPTER 21   1.620000        1320   
118  The eyes of the whole party followed the unexp...   7.150000        1320   
119  Here we have three pair of moccasins, and two ...   3.380000        1320   

     Chapter ID   Utterance ID  
0        134691  000025_000003  
1        134691  000053_000002  
2        134691  000044_000001  
3        134691  000027_000004  
4        134691  000010_000002  
..          ...            ...  
115      122612  000002_000000  
116      122612  000033_000001  
117      122612  000001_000000  
118      122612  000009_000004  
119      122612  000035_000003  

[120 rows x 6 columns]

### Reproduce a random audio of the test dataset

In [ ]:
import IPython
from IPython.display import Audio
import random

directory_path = 'audio/test/*.wav'

# Use glob to get a list of wav files
wav_files = glob.glob(directory_path)
wav_files

audio = random.choice(wav_files)
print(audio)
print(metadata_test_df[metadata_test_df['Audio ID'] == os.path.splitext(os.path.basename(audio))[0]].iloc[0,1])
Audio(audio)

audio/test/1320_122612_000056_000007.wav
In the meantime, the uplifted hand of Hawkeye was above him.


## Obtain Spanish audios

In [ ]:
# Upload zip containing the files

# Extract files
!unzip Jorge_TFM.zip

Archive:  Jorge_TFM.zip
   creating: Jorge_TFM/locutor1/
  inflating: Jorge_TFM/locutor1/audio_1375.wav  
  inflating: Jorge_TFM/locutor1/audio_17238_17239_17240_17241.wav  
  inflating: Jorge_TFM/locutor1/audio_24044.wav  
  inflating: Jorge_TFM/locutor1/audio_25082.wav  
  inflating: Jorge_TFM/locutor1/audio_29241.wav  
  inflating: Jorge_TFM/locutor1/audio_33030.wav  
  inflating: Jorge_TFM/locutor1/audio_33080.wav  
  inflating: Jorge_TFM/locutor1/audio_33442.wav  
  inflating: Jorge_TFM/locutor1/audio_36237_36238_36239_36240.wav  
  inflating: Jorge_TFM/locutor1/audio_36838.wav  
  inflating: Jorge_TFM/locutor1/audio_36945.wav  
  inflating: Jorge_TFM/locutor1/audio_37754_37755.wav  
  inflating: Jorge_TFM/locutor1/audio_40372.wav  
  inflating: Jorge_TFM/locutor1/audio_42328_42329.wav  
  inflating: Jorge_TFM/locutor1/audio_45678_45679.wav  
  inflating: Jorge_TFM/locutor1/audio_47636_47637.wav  
  inflating: Jorge_TFM/locutor1/audio_48613.wav  
  inflating: Jorge_TFM/locutor1/au

In [ ]:
def create_spanish_dataset(source_directory, destination_directory, min_duration=0):

  # Create destination directory if it does not exist
  os.makedirs(destination_directory, exist_ok=True)

  # List all WAV files in the source directory and its subdirectories
  wav_files = glob.glob(os.path.join(source_directory, '**/*.wav'), recursive=True)

  # Create a DataFrame with audio ID and its transcriptions
  transcriptions_df = pd.DataFrame(columns=['Audio ID', 'Original text'])

  # Fill destination_directory directory with audios of more than min_duration (in seconds) and fill transcriptions_df
  for wav_file in wav_files:
    duration = get_audio_length(wav_file)

    if duration > min_duration:
      speaker_id = wav_file.split('/')[-2]

      shutil.copy(wav_file, destination_directory)

      audio_num = os.path.splitext(os.path.basename(wav_file))[0]
      audio_id =  speaker_id + '_' + audio_num

      metadata_path = os.path.join(source_directory, speaker_id, 'metadata_' + speaker_id + '.txt')
      metadata_speaker_id = pd.read_csv(metadata_path, sep='|', header=None, names=['audio_num', 'Original text'])
      original_text = metadata_speaker_id[metadata_speaker_id['audio_num'] == audio_num].iloc[0, 1]

      new_row = pd.DataFrame({'Audio ID':[audio_id],
                              'Original text': [original_text],
                              'Duration': [duration],
                              'Speaker ID': [speaker_id]
                              })

      transcriptions_df = pd.concat([transcriptions_df, new_row])
      os.rename(os.path.join(destination_directory, audio_num + '.wav'), os.path.join(destination_directory, speaker_id + '_' + audio_num + '.wav'))

  n_files = len(os.listdir(destination_directory))
  print(f"{n_files} WAV files copied to " + destination_directory)
  transcriptions_df.reset_index(drop=True, inplace=True)

  transcriptions_df.to_csv(destination_directory + '_metadata.csv', index=False)

In [ ]:
# shutil.rmtree('audio/Spanish')

In [ ]:
destination_directory = 'audio/Spanish'
create_spanish_dataset(source_directory='Jorge_TFM', destination_directory=destination_directory, min_duration=0)

137 WAV files copied to audio/Spanish


In [ ]:
metadata_spanish_df = pd.read_csv(destination_directory + '_metadata.csv')
metadata_spanish_df

Audio ID  \
0                locutor1_audio_37754_37755   
1                      locutor1_audio_36838   
2                       locutor1_audio_5807   
3                      locutor1_audio_36945   
4    locutor1_audio_36237_36238_36239_36240   
..                                      ...   
132              locutor6_audio_19456_19457   
133              locutor6_audio_20330_20331   
134              locutor6_audio_21851_21852   
135                    locutor6_audio_27707   
136              locutor6_audio_18756_18757   

                                         Original text   Duration Speaker ID  
0    Una manera de encontrar el detonante apropiado...   8.126984   locutor1  
1    Yo no quiero encasillarme en un estilo de vida...   3.134694   locutor1  
2    Ya se ve cómo en aquella época el espíritu era...   3.192744   locutor1  
3    El anhelo consiste en desear obtener la recomp...   2.902494   locutor1  
4    A estas alturas, ya te habrás dado cuenta de q...   8.637823   locutor1  
..                                                 ...        ...        ...  
132   Eudoxia está en un rincón del cuartito, tan p...  10.913379   locutor6  
133   Como se acuerda de mi hermano de anteriores o...   8.962902   locutor6  
134   Te recuerdo, desagradable y desagradecida chi...  14.489252   locutor6  
135                   Miranda caminaba hacia nosotros.   2.310385   locutor6  
136   Hacemos aspavientos violentos para impedir qu...  12.550385   locutor6  

[137 rows x 4 columns]

In [ ]:
import IPython
from IPython.display import Audio
import random

directory_path = 'audio/Spanish/*.wav'

# Use glob to get a list of wav files
wav_files = glob.glob(directory_path)
wav_files

audio = random.choice(wav_files)
print(audio)
print(metadata_spanish_df[metadata_spanish_df['Audio ID'] == os.path.splitext(os.path.basename(audio))[0]].iloc[0,1])
Audio(audio)

audio/Spanish/locutor6_audio_43770.wav
 —pregunto con el ceño fruncido después de hacer un gran esfuerzo para reponerme y centrarme.


# Download data

In [ ]:
# # Zip folder
# folder_path = 'audio'
# shutil.make_archive(folder_path, 'zip', folder_path)

# # Download the zip file
# from google.colab import files
# files.download('audio.zip')


# Obtain utterances to reproduce

## English sentences

In [ ]:
utterances = pd.read_csv('https://www.openslr.org/resources/136/metadata.csv', sep='|', usecols=['utterance'])['utterance'].tolist()
print('Total utterances: ' + str(len(utterances)))

Total utterances: 1205


## Spanish sentences

In [ ]:
# Obtain utterances in Spanish (let's aks ChatGPT)

utterances_spanish = [
    "Hola, ¿cómo estás?",
    "Buenos días, ¿cómo fue tu noche?",
    "El sol brilla en el cielo azul.",
    "Me encanta programar en Python.",
    "Hoy es un día especial.",
    "La vida es como una bicicleta, para mantener el equilibrio, debes seguir adelante.",
    "¡Felicidades por tus logros!",
    "Mañana es un nuevo día lleno de oportunidades.",
    "La amistad es un tesoro invaluable.",
    "¿Has probado la comida local?",
    "No te preocupes, todo estará bien.",
    "El conocimiento es poder.",
    "¡Vamos a explorar el mundo!",
    "Cada día es una nueva aventura.",
    "Las risas son el mejor remedio.",
    "Aprender es un viaje que nunca termina.",
    "Si puedes soñarlo, puedes lograrlo.",
    "Gracias por estar aquí.",
    "La creatividad es contagiosa, pásala.",
    "Disfruta de las pequeñas cosas de la vida.",
    "La perseverancia supera la resistencia.",
    "Nunca dejes de aprender.",
    "El trabajo en equipo hace el sueño realidad.",
    "Hoy es un regalo, por eso se llama presente.",
    "Sé la mejor versión de ti mismo.",
    "La paciencia es la clave del éxito.",
    "La familia es lo más importante.",
    "¡Vamos a hacer del mundo un lugar mejor!",
    "Cuando te levantas por la mañana, piensa en el precioso privilegio de estar vivo, de respirar, de pensar, de disfrutar, de amar.",
    "La verdadera medida de la grandeza de un hombre no se encuentra en los momentos de comodidad y conveniencia, sino en los desafíos y controversias.",
    "La vida es un viaje que debe ser vivido con valentía y curiosidad. Cada día presenta nuevas oportunidades para crecer y aprender.",
    "La amistad verdadera es un tesoro invaluable que ilumina los días oscuros y comparte las alegrías más brillantes.",
    "No hay barrera, cerradura ni cerrojo que puedas imponer a la libertad de mi mente.",
    "El éxito no es la clave de la felicidad. La felicidad es la clave del éxito. Si amas lo que haces, tendrás éxito.",
    "La paciencia es la fortaleza del débil y la impaciencia, la debilidad del fuerte.",
    "Las decisiones más difíciles en la vida a menudo resultan en las experiencias más gratificantes.",
    "A veces, las tormentas más difíciles llevan a los arcoíris más hermosos.",
    "El conocimiento es como un jardín: si no se cultiva, no se puede cosechar.",
    "La creatividad no tiene límites. Cuanto más sueñas, más lejos llegas.",
    "La verdadera belleza radica en la aceptación y celebración de nuestras diferencias.",
    "La música es el lenguaje universal que conecta corazones y eleva el espíritu.",
    "La perseverancia es la clave para superar los desafíos y alcanzar tus metas más audaces.",
    "Las mejores historias comienzan con un paso fuera de la zona de confort.",
    "Cada día es una oportunidad para crear recuerdos que durarán toda la vida.",
    "La empatía es la fuerza que une a la humanidad, recordándonos que todos compartimos esta jornada llamada vida.",
    "La humildad es la base sobre la cual se construyen las torres de logro más grandes.",
    "El amor propio es el punto de partida para construir relaciones saludables y significativas con los demás.",
    "La vida es como un libro. Quien no viaja, solo lee la primera página.",
    "La verdadera grandeza se encuentra en la generosidad y el servicio a los demás.",
    "Nuestros errores no definen quiénes somos; son oportunidades para aprender y crecer.",
    "La risa es el mejor remedio para el alma cansada. Encuentra razones para reír todos los días.",
    "La educación es el camino hacia el entendimiento y el progreso en la sociedad.",
    "Las mejores lecciones de vida a menudo se aprenden a través de la adversidad y los desafíos.",
    "La naturaleza nos enseña lecciones de humildad y asombro con cada amanecer y puesta de sol.",
    "El coraje no siempre ruge. A veces, el coraje es esa voz tranquila al final del día que dice: lo intentaré de nuevo mañana.",
    "El respeto es el cimiento de relaciones sólidas y equitativas.",
    "El perdón no excusa el comportamiento, pero libera al que perdona de la carga del resentimiento.",
    "La gratitud convierte lo que tenemos en suficiente y más.",
    "La vida es un lienzo en blanco; cada elección es un trazo que da forma a nuestro destino.",
    "El cambio es la única constante en la vida. Adaptarse es la clave para sobresalir.",
    "La diversidad no solo agrega color al mundo, sino también perspectiva y sabiduría.",
    "El tiempo es el recurso más valioso. Inviértelo sabiamente en lo que realmente importa.",
    "La felicidad no es una meta; es un viaje que se disfruta paso a paso.",
    "La valentía no siempre implica acciones heroicas; a veces, simplemente significa levantarse y enfrentar el día.",
    "La colaboración y el trabajo en equipo multiplican la fuerza y la creatividad individual.",
    "La emoción más hermosa es la que no puede ser explicada con palabras: el amor.",
    "Cada encuentro, incluso el más breve, puede dejar una impresión duradera. Elige ser amable.",
    "La paz interior es el regalo más preciado que puedes darte a ti mismo.",
    "Explora el mundo con ojos curiosos y descubrirás maravillas en cada rincón.",
    "A veces, la lluvia más fuerte produce los arcoíris más brillantes.",
    "No temas a los cambios; a menudo son el preludio de algo grandioso.",
    "Cada día es una nueva página en tu historia. Escribe una buena.",
    "La amistad es como una flor; cuidarla y regarla la hace florecer aún más hermosa.",
    "La paciencia es una virtud que transforma desafíos en logros.",
    "En la simplicidad encontramos la verdadera esencia de la vida.",
    "La música es el lenguaje universal que conecta corazones de todo el mundo.",
    "Sé la luz que ilumina el camino para otros en tiempos de oscuridad.",
    "La creatividad es la chispa que enciende la llama de la innovación.",
    "La libertad no es solo una palabra; es un derecho que todos merecemos.",
    "La empatía es el puente que une a las personas, incluso en medio de diferencias.",
    "El aprendizaje continuo es el camino hacia la mejora constante.",
    "A veces, la mejor respuesta es una sonrisa en silencio.",
    "La bondad es un idioma que los sordos pueden escuchar y los ciegos pueden ver.",
    "La perseverancia es la clave que desbloquea puertas aparentemente imposibles.",
    "Cada error es una lección que nos acerca a la maestría.",
    "La honestidad es como un imán; atrae confianza y construye relaciones sólidas.",
    "La imaginación es el lienzo donde los sueños toman vida.",
    "La gratitud convierte lo ordinario en extraordinario.",
    "Amaneció con un cielo pintado de colores cálidos y susurros de la naturaleza.",
    "La ciudad se despertó entre luces titilantes y el bullicio característico de la urbe.",
    "El aroma del café recién preparado llenó la habitación, despertando todos los sentidos.",
    "Entre risas y confidencias, la tarde se deslizó como un cuento de viejos amigos.",
    "El atardecer teñía el horizonte de tonalidades anaranjadas mientras el sol se despedía.",
    "La melodía suave de un piano acompañaba la escena, creando un ambiente íntimo y relajado.",
    "En la cocina, los ingredientes frescos se mezclaban, revelando el arte culinario en cada platillo.",
    "Caminó por senderos desconocidos, explorando lugares que solo existían en mapas antiguos.",
    "Bajo las estrellas, las historias ancestrales cobraron vida, tejidas en la inmensidad del universo.",
    "La brisa marina acariciaba la piel, llevando consigo secretos guardados por las olas del océano.",
    "El rincón de la librería invitaba a sumergirse en mundos imaginarios y personajes inolvidables.",
    "Las risas de los niños en el parque resonaban como la banda sonora de la felicidad compartida.",
    "Con cada pincelada, el lienzo se transformaba en una expresión única de emociones y colores.",
    "La noche susurraba misterios, dejando entrever la magia que se esconde en lo más oscuro.",
    "El mercado vibraba con la energía de comerciantes apasionados y clientes en busca de tesoros.",
    "Las calles adoquinadas contaban historias antiguas, marcadas por el paso del tiempo.",
    "El eco de la risa se desvaneció en el aire, dejando un rastro de momentos compartidos.",
    "Las luces de la ciudad destellaban como estrellas terrenales, iluminando caminos por descubrir.",
    "En el rincón del jardín, las flores bailaban con la brisa, celebrando la belleza efímera de la naturaleza."
    "Hoy me levanté con una pila de tareas y una taza de café que no se acaba nunca.",
    "La pizza del viernes es una tradición sagrada, ¡no puedo resistirme!",
    "¿Alguien más tiene una lista de reproducción que va desde Mozart hasta reguetón?",
    "Vi una serie tan buena anoche que ahora estoy en modo 'esperando la siguiente temporada'.",
    "La vida es demasiado corta para no disfrutar de un buen postre todos los días, ¿verdad?",
    "¿Alguien más se queda despierto hasta tarde viendo videos de gatitos?",
    "El meme que acabo de ver en internet resume mi vida mejor que yo mismo.",
    "Mi plan para el fin de semana: sofá, mantita y películas. ¡Simple y perfecto!",
    "Acabo de descubrir una receta fácil y deliciosa. ¿Adivina quién se siente chef ahora?",
    "Me encontré con mi amigo de la infancia hoy. ¡Qué nostalgia!",
    "Las llamadas de videollamada se han convertido en mi nueva forma favorita de socializar.",
    "Probé hacer ejercicio en casa hoy y ahora me pregunto por qué no lo intenté antes.",
    "Estoy intentando aprender un nuevo idioma, pero mi memoria parece tener otros planes.",
    "Mis planes para esta noche: comida rápida y una maratón de series. ¡Finde perfecto!",
    "Me perdí en las redes sociales y ahora estoy viendo videos de 'life hacks' durante horas.",
    "Estuve organizando mi armario y encontré ropa que ni recordaba tener. Sorpresas de la cuarentena.",
    "Creo que he alcanzado un nuevo nivel de procrastinación, pero no me importa en absoluto.",
    "¿Soy yo o el tiempo vuela cuando estás en internet?",
    "Hice una lista de compras, pero terminé comprando todo menos lo que estaba en la lista. Clásico.",
    "Todavía no entiendo por qué las cosas siempre desaparecen cuando más las necesitas.",
    "A veces me pregunto si las nubes miran hacia abajo y piensan '¡Vaya, ahí va Juan de nuevo!' ☁️",
    "Hoy decidí ser más productivo. Después de tomar una siesta de tres horas, me sentí increíblemente productivo.",
    "No sé si mi café me está hablando o si solo necesito dormir más.",
    "¿Alguien más siente que los lunes deberían ser opcionales?",
    "Intenté hacer ejercicio, pero creo que mi cuerpo entiende eso como un chiste.",
    "A veces me pregunto si las plantas me extrañan cuando me voy de vacaciones.",
    "Estoy convencido de que mi nevera está conectada a Narnia. Dejo algo y desaparece.",
    "Mi nivel de adultez es directamente proporcional a cuánto disfruto comprar cosas para la casa.",
    "Siempre quise ser superhéroe, pero mis superpoderes parecen limitarse a encontrar cosas perdidas.",
    "La vida sería mucho más sencilla si mi despertador tuviera una opción de 'cinco minutos más y te traigo café'. ☕⏰",
    "Me encantaría ser un pájaro solo por el hecho de poder volar y evitar el tráfico.",
    "Creo que mi máquina de café tiene un botón mágico que convierte los lunes en viernes.",
    "Mi hobby es mirar recetas en internet y luego pedir comida a domicilio.",
    "¿Alguien más está en ese nivel de adultez en el que emocionarse por comprar sábanas nuevas es completamente normal?",
    "Hice una lista de cosas por hacer y ahora mi lista de Netflix es más larga que nunca.",
    "Me encanta cómo mi perro me mira como si fuera la persona más interesante del mundo.",
    "Siempre llevo algo de comida en mi bolso porque nunca se sabe cuándo aparecerá el hambre.",
    "La procrastinación es mi deporte favorito. Tal vez mañana practique más.",
    "A veces me pregunto si mi gato se ríe de mis chistes o simplemente se está burlando de mí.",
    "Mi superpoder secreto es recordar nombres de canciones, pero olvidar por qué entré a una habitación.",
    "El café es mi ritual mañanero sagrado.",
    "A veces me pregunto si los pájaros tienen reuniones secretas en los árboles.",
    "La vida sin pizza no sería la misma.",
    "Hoy decidí aprender algo nuevo. Mañana será otro día.",
    "Me encanta cuando encuentro dinero en mis bolsillos que ni siquiera recordaba que tenía.",
    "Creo que mi perro es el único que me comprende completamente.",
    "La lluvia en la ventana y un buen libro son mi plan perfecto.",
    "Las plantas en mi casa probablemente piensan que soy un jardinero terrible.",
    "A veces me sorprendo a mí mismo pensando en situaciones aleatorias mientras miro por la ventana.",
    "Comprar cosas que no necesito en línea es mi habilidad número uno.",
    "Estoy convencido de que mi gato tiene una vida secreta cuando no estoy en casa.",
    "La mejor parte de la mañana es ese primer sorbo de café.",
    "Hice una lista de tareas pendientes, pero la tarea más importante es ignorar la lista y relajarme.",
    "Nunca he entendido completamente por qué las tostadas siempre caen con el lado de la mantequilla hacia abajo.",
    "La creatividad ataca justo cuando estoy a punto de quedarme dormido.",
    "Siempre he querido ser capaz de hacer una tortilla perfecta, pero siempre termina siendo revuelto.",
    "La música tiene el poder de transportarme a otro lugar en el tiempo.",
    "Una silla cómoda y una buena película son la combinación perfecta para una tarde tranquila.",
    "La simplicidad de un paseo por el parque puede ser revitalizante.",
    "Creo que todos tenemos un superpoder secreto; el mío es recordar nombres de películas al azar.",
    "Bajo el cielo estrellado, susurros de secretos antiguos se deslizaban en el viento nocturno.",
    "En el rincón más oscuro de la ciudad, donde las sombras tejían historias de infortunio, se encontraba su destino.",
    "Ella llevaba consigo el peso de un pasado no contado, sus ojos reflejaban las cicatrices de amores perdidos.",
    "Las calles empedradas resonaban con el eco de pasos solitarios, cada uno contando una historia no dicha.",
    "El café en la taza se enfriaba mientras esperaba en silencio, anhelando respuestas que se escondían en las sombras.",
    "Las luces de la ciudad parpadeaban como luciérnagas perdidas en la vastedad de la noche urbana.",
    "Caminaron juntos por el camino polvoriento, susurros de hojas susurrando secretos que solo el viento entendía.",
    "La luna se reflejaba en el río, revelando destellos de misterio que se deslizaban bajo la superficie tranquila.",
    "Entre los pasillos de la biblioteca antigua, descubrió un libro olvidado que guardaba secretos de vidas pasadas.",
    "Las miradas se cruzaron en la penumbra, desatando corrientes invisibles que unían dos almas en el caos de la noche.",
    "Era como si el tiempo se hubiera detenido, suspendido en el aire mientras las estrellas observaban el drama terrenal.",
    "Cada callejón era un capítulo nuevo, cada puerta cerrada ocultaba un episodio aún no revelado.",
    "El sonido de tacones resonaba en el vestíbulo, anunciando la llegada de alguien cuya presencia prometía intriga.",
    "Bajo el farol antiguo, se encontraron, dos extraños destinados a cruzar sus caminos en el laberinto de la existencia.",
    "Las sombras danzaban en las paredes, como personajes de una tragedia silenciosa que solo las piedras recordarían.",
    "En el rincón del café, las palabras fluyeron como un río, llevando consigo fragmentos de historias entrelazadas.",
    "El crepúsculo pintaba el cielo con tonalidades de naranja y rosa mientras ella caminaba hacia el horizonte desconocido.",
    "A través de la ventana entreabierta, la melodía de un piano solitario llenaba la habitación, creando un eco de melancolía.",
    "Las hojas crujían bajo sus pies mientras exploraba el bosque prohibido, donde los susurros de la naturaleza revelaban secretos ocultos.",
    "En el rincón polvoriento de la librería de segunda mano, encontró un diario antiguo lleno de cartas de amor perdidas en el tiempo.",
    "Las olas del mar susurraban cuentos antiguos a la orilla, mientras la luna observaba en silencio desde su trono celestial.",
    "En el café de la esquina, las tazas de té compartían susurros de confidencias, convirtiendo cada sorbo en un pacto silencioso.",
    "A medida que el reloj avanzaba, las sombras en la pared contaban la historia de un día que se desvanecía en la oscuridad.",
    "La anciana del parque tejía recuerdos en su bufanda mientras el viento llevaba fragmentos de su vida hacia el horizonte.",
    "El faro solitario en el acantilado iluminaba la noche, guiando a los barcos perdidos hacia un puerto seguro en medio de la tormenta.",
    "Bajo el manzano en flor, el aroma dulce del amor se mezclaba con la brisa primaveral, tejiendo promesas en el aire fresco.",
    "Las páginas del libro antiguo crujían con cada vuelta, revelando una historia olvidada que aguardaba pacientemente su redescubrimiento.",
    "Entre las sombras del callejón, se gestaba un romance clandestino, susurros y miradas furtivas que desafiaban el destino.",
    "Las lágrimas en sus ojos reflejaban tormentas internas, mientras el cielo lloraba en sintonía con los pesares del alma.",
    "A orillas del río, dos almas errantes se encontraron, intercambiando historias como piedras que saltan en la superficie del agua.",
    "La vela parpadeaba en la ventana, esperando el regreso de alguien cuya ausencia había dejado cicatrices en el corazón.",
    "En el mirador de la ciudad, las luces destellaban como estrellas urbanas, cada destello contando una historia única en la vastedad nocturna.",
    "Bajo el cielo estrellado, sus pasos resonaban en el silencio de la noche, un baile íntimo con la quietud.",
    "El aroma del café flotaba en el aire, tejiendo recuerdos de conversaciones compartidas y miradas cómplices.",
    "La risa de los niños en el parque resonaba como melodía alegre, pintando sonrisas en los rostros de quienes los observaban.",
    "En la calle bulliciosa, los colores vibrantes de los escaparates invitaban a un viaje visual por mundos llenos de posibilidades.",
    "Bajo el dosel de hojas doradas, un banco solitario esperaba a alguien dispuesto a intercambiar sus pensamientos con el viento.",
    "Atravesando el umbral, descubrió un rincón de nostalgia en cada antiguo vinilo que descansaba en la estantería polvorienta.",
    "Las mariposas danzaban en el jardín, llevando secretos de amor entre las flores que balanceaban sus cabezas al compás del viento.",
    "La luz del atardecer acariciaba las fachadas de los edificios, transformando la ciudad en un lienzo de colores cálidos.",
    "Con cada palabra escrita, la pluma dejaba un rastro de emociones en el papel, un diálogo silencioso entre el autor y sus pensamientos.",
    "Los faroles en la plaza titilaban con un encanto antiguo, guiando a los transeúntes por senderos iluminados por la historia.",
    "En el rincón de la biblioteca, el susurro de páginas girando narraba cuentos de dragones, héroes y mundos más allá del alcance de la realidad.",
    "El eco lejano de una guitarra callejera se mezclaba con el bullicio urbano, creando una sinfonía improvisada en las calles transitadas.",
    "Las hojas caídas crujían bajo los pasos, marcando el inicio de una nueva estación y el fin de un capítulo en el libro del tiempo.",
    "Al borde del acantilado, el horizonte se fundía con el mar, un lienzo infinito donde el sol y el agua compartían su danza eterna.",
    "Las luciérnagas destellaban en la penumbra, pequeñas estrellas terrestres guiando a los soñadores hacia mundos de ensueño.",
    "En el café con aroma a tinta fresca, las páginas de un nuevo libro esperaban ansiosas ser exploradas por mentes curiosas.",
    "En las noticias de hoy, analizamos el impacto de las recientes decisiones gubernamentales en la economía nacional.",
    "El reportero en el terreno nos trae imágenes exclusivas de las protestas que han tenido lugar en el centro de la ciudad.",
    "Hacemos un seguimiento de las últimas cifras de la pandemia, destacando las medidas tomadas para frenar la propagación del virus.",
    "Entrevistamos a expertos para obtener perspectivas sobre el cambio climático y sus posibles consecuencias a nivel global.",
    "En el ámbito deportivo, repasamos los resultados y momentos destacados de la jornada en diversas disciplinas.",
    "Informamos sobre los avances en la investigación de importantes casos criminales que han capturado la atención del público.",
    "El corresponsal internacional nos conecta con los acontecimientos más relevantes en diferentes partes del mundo.",
    "Destacamos las iniciativas sociales y solidarias que buscan mejorar la calidad de vida de comunidades menos favorecidas.",
    "En cultura, exploramos los eventos y exposiciones que enriquecen el panorama artístico y creativo de nuestra sociedad.",
    "El análisis político de hoy examina los últimos movimientos en el escenario político nacional e internacional.",
    "La sección de tecnología presenta las últimas innovaciones y tendencias que están transformando nuestra forma de vivir y trabajar.",
    "Cerramos con una nota positiva, compartiendo historias inspiradoras de superación y logros personales.",
    "Hola, ¿qué tal? ¿Alguien más ama los días lluviosos?",
    "¡Guau, no puedo creer lo que acabo de ver en la tele!",
    "Oye, ¿alguna recomendación para una película emocionante?",
    "¿Has probado ese nuevo café del centro? Está genial.",
    "¡Vaya día agitado! Necesito unas vacaciones urgentes.",
    "¿Has visto el último episodio de esa serie? ¡Fue increíble!",
    "¡Buenos días! ¿Alguien más necesita café para empezar el día?",
    "¡Uy, se me olvidó completamente la reunión! ¿Puedo recuperarlo?",
    "¿Alguien tiene planes emocionantes para el fin de semana?",
    "Estoy tan emocionado por las vacaciones que ya estoy haciendo la maleta mentalmente.",
    "¡Hola a todos! ¿Cómo están?",
    "No puedo creer lo rápido que pasa el tiempo.",
    "¿Alguien más tiene antojo de pizza?",
    "¡Qué día tan loco! Necesito un descanso.",
    "Me encanta esa canción, ¿la has escuchado?",
    "¡Guau, este nuevo videojuego es asombroso!",
    "¿Alguien quiere unirse a mí para una tarde de películas?",
    "¡Saludos desde el otro lado de la pantalla!",
    "Hoy es uno de esos días en los que todo está yendo mal.",
    "¿Ya viste el último episodio de esa serie? Fue impactante.",
    "¡Buenas noticias! ¡Me dieron el trabajo!",
    "¿Algún amante del café por aquí?",
    "La lluvia siempre me pone melancólico.",
    "¡Ay, mi teléfono está lleno de memes graciosos!",
    "¿Quién más está contando los días para el fin de semana?",
    "¿Alguna sugerencia para una nueva serie?",
    "La vida sería aburrida sin música.",
    "¿Han probado esa nueva heladería? ¡Es espectacular!",
    "Nunca es tarde para un cambio de imagen.",
    "A veces, solo necesitas un día de descanso completo.",
    "¿Cuál es tu lugar favorito para relajarte?",
    "Estoy pensando en empezar un nuevo hobby. ¿Algún consejo?",
    "¡Oops! Olvidé comprar leche en el supermercado.",
    "La risa es la mejor medicina, ¿no creen?",
    "Estoy tan emocionado por las vacaciones que ya estoy haciendo planes.",
    "¡Hola, mi gente! ¿Qué se traen entre manos?",
    "¿Cuál es tu comida reconfortante favorita?",
    "A veces, una simple sonrisa puede alegrar el día de alguien.",
    "¿Alguna película recomendada para ver en casa?",
    "¡Increíble cómo las cosas pueden cambiar en un instante!",
    "¡Buena vibra para todos en este día!",
    "¿Alguien más tiene una lista de reproducción para cada estado de ánimo?",
    "¡Es viernes! ¿Planes para el fin de semana?",
    "¿Ya es hora de una siesta? ¡Sí, por favor!",
    "A medida que avanzamos en la vida, aprendemos que las batallas más difíciles a menudo van de la mano con las mejores recompensas.",
    "En este vasto universo, cada uno de nosotros es solo una pequeña chispa, pero juntos podemos iluminar el cielo nocturno.",
    "El arte de vivir está en encontrar la belleza en los pequeños detalles, en disfrutar de los momentos simples que la vida nos ofrece.",
    "Cuando enfrentamos desafíos, no solo descubrimos nuestra fuerza interior, sino también la capacidad de superar cualquier adversidad.",
    "La amistad verdadera es como una estrella en el cielo: aunque no siempre la ves, sabes que siempre está ahí, iluminando tu vida.",
    "Cada página en blanco es una nueva oportunidad para escribir tu historia, para crear un capítulo lleno de aventuras y descubrimientos.",
    "A veces, la clave para la felicidad radica en aprender a bailar bajo la lluvia en lugar de esperar a que pase la tormenta.",
    "El amor es un jardín que florece con el tiempo y la dedicación, donde cada pétalo representa un hermoso recuerdo compartido.",
    "La paciencia es como una semilla que plantamos hoy y cosechamos mañana, recordándonos que las cosas buenas llevan tiempo.",
    "En la sinfonía de la vida, cada elección que hacemos es una nota que contribuye a la melodía única que nos define.",
    "La magia de los sueños está en la posibilidad de convertir lo imposible en algo alcanzable, llevándonos a lugares donde nunca imaginamos llegar.",
    "A lo largo de la vida, cruzamos caminos con personas que dejan una huella imborrable en nuestro corazón, recordándonos la importancia de cada encuentro.",
    "La risa es el idioma universal que conecta corazones y almas, recordándonos que la felicidad es una expresión que todos entendemos.",
    "Cada día es una nueva oportunidad para aprender, crecer y convertirnos en la mejor versión de nosotros mismos. ¡Aprovechemos cada momento!",
    "La gratitud es como un faro que ilumina nuestro camino, recordándonos apreciar las pequeñas alegrías que la vida nos ofrece a diario.",
    "A veces, las palabras no son suficientes para expresar lo que sentimos, pero un abrazo sincero puede transmitir más amor que mil palabras.",
    "En el vasto lienzo de la existencia, cada experiencia, ya sea de alegría o dolor, contribuye a pintar el hermoso cuadro de nuestra vida.",
    "La vida es un poema, y cada día es una oportunidad para agregar versos llenos de amor, compasión y significado.",
    "La autenticidad es la llave que desbloquea puertas hacia relaciones significativas y una vida llena de propósito.",
    "A medida que caminamos por el sendero de la vida, recordemos disfrutar del paisaje, aprender de los desafíos y celebrar los pequeños triunfos.",
    "La maravilla de la vida está en la diversidad de experiencias que podemos vivir, enriqueciendo nuestro viaje con colores y texturas únicas.",
    "A veces, las respuestas que buscamos se encuentran en los silencios, en la calma interior que nos permite escuchar la sabiduría de nuestro propio ser.",
    "La empatía es el puente que conecta corazones, recordándonos que, al comprender la experiencia del otro, construimos puentes hacia la comprensión mutua.",
    "Los recuerdos son tesoros que atesoramos en el cofre de nuestra mente, cada uno contando una historia única de nuestras travesías por la vida.",
    "En la danza de la existencia, cada elección que hacemos es un paso, guiándonos a través de movimientos gráciles y desafíos que nos hacen más fuertes.",
    "La resiliencia es como un árbol que dobla sus ramas ante la tormenta pero permanece firme enraizado en la tierra, recordándonos nuestra propia fortaleza interior.",
    "Cada amanecer es un lienzo en blanco que la vida nos regala, invitándonos a pintar con los pinceles de la esperanza y la positividad.",
    "La verdadera riqueza no se mide en posesiones materiales, sino en la calidad de nuestras relaciones, en los momentos compartidos y en el amor que damos y recibimos.",
    "La paciencia es una lección que la naturaleza nos enseña cada temporada, recordándonos que incluso las flores más hermosas necesitan tiempo para florecer.",
    "La curiosidad es el faro que nos guía hacia nuevos horizontes, revelando secretos ocultos y despertando el deseo eterno de explorar el vasto universo.",
    "La compasión es un bálsamo suave que sana heridas invisibles, extendiendo un abrazo invisible que reconoce la humanidad compartida en cada uno de nosotros.",
    "Cada desafío que enfrentamos es una oportunidad disfrazada, una posibilidad de crecer, aprender y descubrir la fuerza interior que ni siquiera sabíamos que teníamos.",
    "La gratitud es el sol radiante que disipa las nubes de la negatividad, iluminando nuestro mundo con una luz cálida que resalta las bendiciones que nos rodean.",
    "La familia es el cimiento sobre el cual construimos nuestras vidas, un refugio seguro que nos abraza en los días oscuros y celebra con nosotros en los días luminosos.",
    "El perdón es un regalo que nos damos a nosotros mismos, liberándonos de las cadenas del resentimiento y permitiéndonos avanzar con ligereza hacia un futuro más luminoso.",
    "La creatividad es la chispa que enciende la llama de la innovación, permitiéndonos ver el mundo con nuevos ojos y transformar lo ordinario en algo extraordinario.",
    "La educación es el faro que guía el barco de la vida, iluminando el camino hacia el conocimiento, la comprensión y el poder de cambiar el mundo.",
    "La serenidad es un estado interior de paz que encontramos al aceptar lo que no podemos cambiar y alabarnos por el coraje de cambiar lo que podemos.",
    "La solidaridad es el lazo invisible que une a la humanidad, recordándonos que, juntos, podemos superar desafíos, construir puentes y crear un mundo más compasivo.",
    "La vida es un caleidoscopio de momentos, cada uno único en su belleza efímera, recordándonos que, al apreciar el presente, creamos un futuro lleno de colores vibrantes.",
    "La sabiduría está tejida en las historias que compartimos, en las lecciones que aprendemos y en la humildad que nos guía hacia un entendimiento más profundo de la existencia.",
    "En el rincón silencioso de la noche, las estrellas son testigos de nuestras reflexiones más íntimas, iluminando secretos que solo la oscuridad conoce.",
    "El viaje de la vida nos lleva por caminos serpenteantes, entre montañas de alegrías y valles de desafíos, pero cada paso es una oportunidad de descubrimiento.",
    "Bajo el manto del crepúsculo, las sombras danzan en complicidad con la luz, creando un espectáculo celestial que nos invita a apreciar la belleza efímera del día.",
    "La lluvia, suave caricia del cielo, acaricia la tierra sedienta, nutriendo cada rincón con la promesa de renacimiento y la sinfonía de gotas danzantes.",
    "En el escenario de la existencia, cada encuentro es una actuación única, donde los protagonistas entrelazan sus historias, dejando huellas en el telar del tiempo.",
    "El eco de las risas resuena en el viento, recordándonos que la felicidad es una melodía compartida que se expande cuando la compartimos con otros.",
    "Los sueños son estrellas fugaces en la bóveda celeste de nuestra imaginación, guiándonos hacia horizontes inexplorados llenos de posibilidades infinitas.",
    "Bajo la sombra de la arboleda ancestral, los susurros del viento nos cuentan historias olvidadas, mientras las hojas crujen como páginas de un libro antiguo.",
    "La amistad es un jardín floreciente, donde las risas son las flores que embellecen cada rincón y el cariño es la lluvia que nutre la raíz de la conexión.",
    "En el tejido de la memoria, las experiencias se entrelazan como hilos de colores, creando un tapiz único que contamos y compartimos a lo largo de nuestra vida.",
    "La madurez es un viaje interior que nos lleva de la inocencia a la sabiduría, marcado por cicatrices que cuentan la historia de nuestras batallas ganadas.",
    "La tecnología, ingeniosa aliada del progreso, nos conecta en un mundo digital donde las ideas viajan como electrones, desafiando las barreras del tiempo y el espacio.",
    "En el vaivén de las estaciones, el invierno se viste de blancura, la primavera florece en colores, el verano brilla con intensidad y el otoño pinta paisajes dorados.",
    "La danza de las sombras al atardecer es un poema visual que nos invita a reflexionar sobre la fugacidad del tiempo y la belleza efímera de cada día.",
    "En la sinfonía de la naturaleza, el viento acaricia las hojas como músico talentoso, las olas bailan en el compás del mar y los pájaros componen melodías al vuelo.",
    "La cocina es un laboratorio donde los ingredientes se transforman en obras maestras de sabor, y cada receta es un viaje culinario que deleita los sentidos.",
    "El amor, suave melodía que resuena en el corazón, es la fuerza que une almas, rompe barreras y teje historias de complicidad en el lienzo del tiempo.",
    "En el vaivén de la cotidianidad, los pequeños momentos se convierten en tesoros que atesoramos en el cofre de nuestros recuerdos, añadiendo brillo a la vida.",
    "¡Hola, qué pasa! ¿Cómo va todo por ahí?",
    "La vida es como una bicicleta, para mantener el equilibrio, debes seguir adelante.",
    "Estar en la chamba a veces es puro cotorreo, pero hay que chambearle.",
    "¡No hay excusas! Todo se arregla con una buena actitud y unos buenos bailoteos.",
    "A veces lo guay de la vida es que no hay pedo en decir 'no' y echarme una buena siesta.",
    "¡Qué lástima! Bueno, a veces la vida es un desmadre, pero hay que echarle ganas.",
    "Solo cuando algo es espectacular, le doy un like y lo comparto, sino no merece la pena.",
    "Cuando se va el internet, es como si te lo quitaran todo. Tienes que aprender a sobrevivir.",
    "A veces la suerte está de nuestro lado y todo sale de puta madre, ¿verdad?",
    "Nada como comerse un buen durum y sentir que la vida merece la pena.",
    "¡Qué pena! Pero bueno, la vida es corta, así que hay que recomponerse y darlo todo.",
    "Estar al cien es la meta, pero a veces estar al cincuenta está más que bien.",
    "No hay fecha que no se cumpla ni deuda que no se pague. Así es la vida, tío.",
    "¡Venga ya! A disfrutar del buen rollo y de los momentazos que nos da la vida.",
    "¡Oye! Que la vida son dos días, hay que vivirla con alegría.",
    "Cuando algo es muy divertido, se dice que es la bomba. ¡Estuvo la bomba!",
    "Estar en las nubes es normal de vez en cuando, pero hay que bajar a la Tierra.",
    "A veces las cosas se tuercen, pero no pasa nada, ya se enderezarán.",
    "¡Anda ya! Siempre hay alguien que se pasa de listo, pero se le pilla rápido.",
    "Estar a dos velas no mola nada, pero ya vendrán tiempos mejores.",
    "Si algo es complicado, se dice que es un lío. ¡Menudo lío se ha montado!",
    "A veces hay que ponerse las pilas y currar un poco más. Así es la vida.",
    "Estar hasta las narices de algo es normal, pero hay que aguantarse.",
    "Cuando algo es raro o extraño, se dice que es de otro mundo. ¡Es de otro mundo!",
    "Estar en las mismas es difícil de evitar, pero se intenta.",
    "¡Qué va! A veces hay que decir que no a las complicaciones y disfrutar.",
    "Estar en las nubes es normal de vez en cuando, pero hay que bajar a la Tierra.",
    "A veces hay que soltar una parrafada para que se entienda bien.",
    "¡Cálmate! No merece la pena perder los nervios por tonterías.",
    "A veces la vida es un poco cuesta arriba, pero se sube igualmente.",
    "Si algo está claro, se dice que está cantado. ¡Está cantado que vamos a triunfar!",
    "¡Qué jaleo! A veces todo se lía, pero al final se arregla.",
    "Estar en las nubes es normal de vez en cuando, pero hay que bajar a la Tierra.",
    "¡Qué morro tiene! Hay gente que pide mucho sin dar nada a cambio.",
    "Estar en las mismas es difícil de evitar, pero se intenta.",
    "Si algo es complicado, se dice que es un lío. ¡Menudo lío se ha montado!",
    "Bajo la luz de la luna, susurros de secretos antiguos se deslizaban por el viento.",
    "En el bullicio de la ciudad, encontré la paz en el susurro de las hojas de los árboles.",
    "Las estrellas brillaban en el cielo como diamantes incrustados en la bóveda celeste.",
    "Caminé por la playa, donde las olas susurraban historias de navegantes y misterios marinos.",
    "El aroma del café recién hecho llenaba la habitación, despertando mis sentidos.",
    "En la quietud de la noche, el murmullo del río se convertía en una sinfonía nocturna.",
    "A medida que el sol se ocultaba en el horizonte, el cielo se tiñó de tonos cálidos y dorados.",
    "Las montañas se alzaban majestuosas, testigos silenciosos de la grandeza de la naturaleza.",
    "Bajo la lluvia, las calles brillaban como un lienzo reflejando las luces de la ciudad.",
    "En la penumbra, las sombras danzaban en una danza silenciosa, creando un juego de luces y sombras.",
    "El viento susurraba secretos a los árboles, mientras las hojas bailaban en su suave caricia.",
    "Atravesé el bosque, donde los rayos del sol se filtraban entre las ramas, pintando el suelo de luces y sombras.",
    "Al llegar la primavera, los campos se llenaron de colores vivos y el aroma de las flores llenó el aire.",
    "Cerré los ojos y dejé que la música me llevara a lugares lejanos, donde los sueños se vuelven realidad.",
    "En la vastedad del océano, las olas contaban historias de viajes y aventuras que quedaron grabadas en la memoria del mar.",
    "En la cafetería, el aroma del café mezclado con risas llenaba el aire.",
    "Durante la lluvia, la ciudad adquiría un brillo especial bajo las luces de la calle.",
    "La rutina diaria se rompió con una noticia inesperada que cambió el rumbo de sus días.",
    "En la sala de espera, el tic tac del reloj marcaba el tiempo con impaciencia.",
    "Las conversaciones en la mesa del comedor eran el eco de historias cotidianas y anécdotas familiares.",
    "Bajo las luces tenues de la calle, los vecinos compartían saludos cordiales al volver a casa.",
    "El tráfico urbano creaba un vaivén constante de luces y sonidos en la bulliciosa ciudad.",
    "En la oficina, el sonido de teclados y teléfonos creaba una sinfonía moderna de productividad.",
    "El amanecer en la playa pintaba el cielo con tonos suaves mientras los madrugadores disfrutaban de la calma.",
    "La brisa fresca del parque llevaba consigo risas de niños y el canto de pájaros en los árboles.",
    "En el supermercado, el bullicio de carros y conversaciones creaba un telón de fondo para la vida cotidiana.",
    "El calor del sol acariciaba la piel durante un día de verano en el campo.",
    "Las charlas en la esquina del café revelaban los encuentros casuales que dan color a la vida urbana.",
    "La reunión de amigos en la terraza estaba acompañada por risas, música y el chisporroteo de una parrilla.",
    "En la biblioteca, el susurro de páginas al pasar creaba una sinfonía silenciosa para los amantes de la lectura.",
    "¡Hola, mundo!",
    "Cuando tienes un día largo, el café es tu mejor amigo.",
    "¿Alguien más se siente como si el viernes debería ser parte del fin de semana?",
    "Esa sensación cuando encuentras el meme perfecto para la situación.",
    "¿Netflix y pizza? Sí, por favor.",
    "Cuando te das cuenta de que tienes más memes en tu teléfono que fotos de vacaciones.",
    "La vida es corta. Come postre primero.",
    "Intentando recordar la contraseña después de cambiarla: una historia de terror moderna.",
    "La procrastinación nivel experto: leyendo sobre cómo vencer la procrastinación en lugar de hacerlo.",
    "El lunes debería ser opcional, ¿no crees?",
    "Ese momento incómodo cuando saludaste a alguien pensando que te estaba saludando a ti.",
    "Mi plan para hoy: sobrevivir.",
    "¿Por qué no hay emoticonos para el café?",
    "Cuando alguien dice que no le gusta el chocolate, siempre miro dos veces.",
    "La vida es demasiado corta para no disfrutar de un buen helado.",
    "La creatividad es contagiosa, pásala.",
    "Vive el momento, ¡es todo lo que tienes!",
    "A veces, la música es la única terapia que necesitas.",
    "La vida es como andar en bicicleta: para mantener el equilibrio, debes seguir adelante.",
    "Nunca es tarde para ser lo que podrías haber sido.",
    "Haz el bien y deja una huella positiva.",
    "La felicidad es un viaje, no un destino.",
    "Sé la razón por la que alguien sonríe hoy.",
    "Si te caes siete veces, levántate ocho.",
    "No cuentes los días, haz que los días cuenten.",
    "A veces, la solución es tomarse un descanso y respirar.",
    "El café y la confianza te ayudan a conquistar el día.",
    "Hazlo con pasión o no lo hagas en absoluto.",
    "La vida no es esperar a que pase la tormenta, sino aprender a bailar bajo la lluvia.",
    "La clave de la felicidad está en apreciar lo que tienes mientras trabajas por lo que quieres.",
    "Cuando nada es seguro, todo es posible.",
    "El éxito es la suma de pequeños esfuerzos repetidos día tras día.",
    "La vida es corta, sonríele a quien lloras, ignora a quien te critica y sé feliz con quien te importa.",
    "No tienes que ser positivo todo el tiempo. Es perfectamente normal sentirse triste, enojado, disgustado. Emociones son señales de que eres humano.",
    "La mejor forma de predecir el futuro es crearlo.",
    "Lo único imposible es aquello que no intentas.",
    "No compares tu vida con la de los demás. No tienes ni idea de lo que ha sido su viaje.",
    "Si no puedes hacer grandes cosas, haz cosas pequeñas de una forma grandiosa.",
    "A veces, la risa es la única terapia que necesitas.",
    "La paciencia es la clave del cielo.",
    "No esperes a tener todo listo para disfrutar tu viaje.",
    "Vive la vida con intensidad, no con prisa.",
    "Nunca es tarde para empezar de nuevo.",
    "Haz de hoy tu día. Crea tu propia suerte.",
    "No cuentes los días, haz que los días cuenten.",
    "Aprende a decir 'no' sin sentirte culpable.",
    "Oye, ¿te cuento un secreto? A veces creo que las nubes son como los sueños: cambian de forma pero siempre están ahí.",
    "Ey, ¿alguna vez te has preguntado por qué las pizzas redondas vienen en cajas cuadradas? Es como, un misterio del universo, ¿no?",
    "Chaval, hoy fue un día de locos. Estuve en el supermercado y juraría que las frutas estaban conspirando para saltar al carrito ellas solas.",
    "¿Sabes qué? No hay nada como llegar a casa, ponerse cómodo y disfrutar de una buena serie. Netflix es mi mejor amigo, ¡sin duda!",
    "Amigo, ¿alguna vez has tenido la sensación de que tu gato te mira con desprecio? No sé qué le pasa, pero creo que le caigo mal.",
    "¡Vaya día! Estuve intentando cocinar algo diferente y al final acabé con un desastre en la cocina. ¿Te crees que alguien entiende las recetas?",
    "Chisme del día: vi a la vecina bailando salsa en su sala. No sé si estaba practicando para un concurso o simplemente disfrutando de la vida.",
    "Hoy fui al gimnasio con la idea de hacer ejercicio, pero terminé más tiempo en la máquina de snacks que en la cinta. Mis prioridades son claras.",
    "¿Te ha pasado que cuando buscas algo, no lo encuentras, pero cuando dejas de buscarlo, aparece de la nada? Mi vida en una frase.",
    "¡Ey, tío! Anoche tuve un sueño tan raro que hasta las palomitas de maíz en mi cabeza estaban confundidas. No sé qué cenan mis pensamientos, pero debe ser divertido.",
    "Hoy me di cuenta de que mi nevera es un portal mágico. Metí restos de pizza y al día siguiente, ¡voilà! ¡Tenía comida nueva!",
    "La vida es como una película. A veces eres el protagonista, otras el extra, y en ocasiones, simplemente estás en la sala comiendo palomitas.",
    "¿Sabías que las plantas son como las mascotas silenciosas? Solo que en lugar de ladrar, crecen. Mis cactus son los más silenciosos de la cuadra.",
    "Tengo una relación de amor-odio con mi despertador. Me despierta, pero no siempre estoy de humor para escuchar su música tan temprano.",
    "Anoche soñé que estaba en una isla desierta rodeado de libros. Fue genial hasta que me desperté y me di cuenta de que los libros eran mi almohada.",
    "La realidad es un lugar interesante, pero a veces prefiero vivir en mis pensamientos. Allí las reglas son más flexibles y los unicornios son reales.",
    "¿Te ha pasado que entras a una habitación y olvidas por qué estabas allí? Mi cerebro debe tener su propio GPS caprichoso.",
    "Las mañanas son como un juego de azar. Puedes despertarte con energía de superhéroe o sentirte como un personaje de película de terror. No hay término medio.",
    "Descubrí que el botón de 'snooze' del despertador es mi mejor amigo y mi peor enemigo. Es tan tentador, pero también tan traicionero.",
    "Hoy intenté seguir una receta gourmet y terminé con una versión peculiar de la cocina molecular. Llamé a mi obra maestra 'Fusión de Desastre Culinary'.",
    "¿Alguna vez te has preguntado por qué los aguacates maduran justo cuando decides que hoy es el día para comer guacamole? La vida es un misterio verde.",
    "Me encanta la lluvia. Es como si el cielo estuviera teniendo su propio concierto de tambores, y nosotros somos la audiencia que aplaude desde adentro.",
    "Hoy intenté ser adulto responsable, pero la nevera vacía y mi amor por las galletas me ganaron. ¡Al menos sé que mi niño interior está bien alimentado!",
    "A veces creo que mi gato es un filósofo disfrazado. Siempre tiene esa mirada reflexiva como si estuviera contemplando el sentido de la vida.",
    "La tecnología y yo tenemos una relación complicada. A veces me hace sentir inteligente, y otras veces, completamente desconcertado.",
    "Intenté hacer ejercicio, pero mi cuerpo dijo 'no gracias' y mi sofá asintió con aprobación. Creo que forman un comité en mi contra.",
    "En mi nevera hay un ecosistema completo. Siempre encuentro cosas que no recuerdo haber comprado. Debe ser la evolución de los restos de comida.",
    "La vida sin café sería como un día sin sol. Aunque, si tengo demasiado café, mi día termina siendo como una película de acción acelerada.",
    "Mi superpoder es recordar todas las letras de las canciones que escuché en mi adolescencia, pero olvidar por qué entré a una habitación.",
    "A veces me pregunto si las plantas piensan en nosotros. Tal vez cuando hablamos con ellas, están diciendo 'aquí viene ese humano de nuevo'.",
    "La creatividad se me presenta a menudo a las 3 a.m., cuando debería estar durmiendo. Es como si mi cerebro operara en un huso horario diferente.",
    "Nunca subestimes el poder curativo de una siesta. Es como un reinicio para el alma, especialmente si tienes una manta suave y una almohada cómoda.",
    "¿Alguna vez has tratado de recordar el nombre de alguien y tu cerebro decide darte la vuelta en lugar de la respuesta? Mi memoria es un laberinto divertido.",
    "Las recetas de cocina son como sugerencias. A veces las sigo al pie de la letra, y otras veces mi cocina se convierte en un laboratorio experimental.",
    "Dicen que la paciencia es una virtud. Intento recordarlo cada vez que estoy atascado en un atasco de tráfico, pero a veces mi paciencia toma vacaciones.",
    "La lluvia es como música para mis oídos. Cada gota es una nota que compone una sinfonía natural. ¿Quién necesita Spotify cuando tienes ventanales mojados?",
    "Mi vida está dividida entre 'antes del café' y 'después del café'. Es la poción mágica que convierte mi mañana en un evento manejable.",
    "La risa es el mejor remedio, especialmente cuando intentas recordar dónde dejaste las llaves del coche.",
    "La procrastinación es como un juego mental en el que siempre pienso que tendré tiempo mañana. Pero, ¿quién puede resistirse al encanto de un buen procrastinación?",
    "Intenté seguir una receta gourmet, pero mi cocina parecía más un campo de batalla culinario. Al final, la pizza de entrega fue mi héroe.",
    "La siesta es como una mini vacación en medio del día. Siempre me pregunto por qué no instituimos siestas obligatorias en el trabajo.",
    "A veces creo que los gatos tienen superpoderes invisibles, como la capacidad de aparecer justo cuando estoy a punto de abrir una lata de atún.",
    "La tecnología avanza tan rápido que a veces siento que mi teléfono es más inteligente que yo. Pero al menos no puede hacer una buena taza de café.",
    "La vida sería mucho más aburrida sin esos momentos inesperados de alegría, como encontrar dinero en un bolsillo olvidado.",
    "El tiempo es relativo, especialmente cuando espero algo emocionante. Un minuto puede sentirse como una eternidad en esa situación.",
    "Nunca subestimes el poder de una sonrisa. Puede iluminar incluso los días más grises, aunque a veces me olvido de sonreír en las fotos.",
    "La música es mi terapia personal. No importa cómo me sienta, siempre hay una canción que puede expresar exactamente lo que necesito escuchar.",
    "En un mundo lleno de tecnología, aún encuentro satisfacción en escribir a mano. Hay algo mágico en ver las palabras tomar vida en el papel.",
    "La cocina es mi espacio creativo. A veces mis experimentos culinarios son un desastre, pero otras veces descubro nuevas recetas que se convierten en mis favoritas.",
    "El caos de mi escritorio refleja la complejidad de mis pensamientos. Aunque siempre sé dónde está todo, incluso si parece un desastre para los demás.",
    "La lluvia y un buen libro hacen una combinación perfecta. Es como si las palabras cobraran vida con el sonido de las gotas golpeando la ventana.",
    "La felicidad se encuentra en las pequeñas cosas, como ese primer sorbo de café por la mañana o el olor a tierra después de la lluvia.",
    "El caos de mi escritorio refleja la complejidad de mis pensamientos. Aunque siempre sé dónde está todo, incluso si parece un desastre para los demás.",
    "La lluvia y un buen libro hacen una combinación perfecta. Es como si las palabras cobraran vida con el sonido de las gotas golpeando la ventana.",
    "La felicidad se encuentra en las pequeñas cosas, como ese primer sorbo de café por la mañana o el olor a tierra después de la lluvia.",
    "La creatividad es como un río que fluye constantemente. A veces solo necesitas sumergirte en sus aguas para encontrar nuevas ideas brillantes.",
    "Las estaciones cambian, pero algunas cosas permanecen constantes. Como el placer de ver una puesta de sol dorada al final del día.",
    "La música tiene el poder de transportarnos a diferentes lugares y momentos. Es como un billete mágico para un viaje emocional.",
    "A veces, las palabras fluyen como un río, mientras que en otras ocasiones se sienten atrapadas en el embalse de la mente. Pero siempre encuentran su camino.",
    "La vida es un rompecabezas en constante evolución. Cada experiencia encaja como una pieza única, formando el hermoso cuadro de nuestra existencia.",
    "La amistad es como un jardín que florece con risas, apoyo y momentos compartidos. Cada amigo es una flor única en este hermoso paisaje.",
    "La aventura aguarda en cada esquina, ya sea en las páginas de un libro, en un rincón desconocido del mundo o en el corazón de una nueva experiencia.",
    "La paciencia es una virtud que a veces olvido, pero siempre me recuerda que las cosas más hermosas toman tiempo para desarrollarse.",
    "Las metas son como faros que nos guían en medio de la oscuridad. Nos impulsan a avanzar, incluso cuando el camino parece difícil.",
    "La gratitud es un regalo que damos a nosotros mismos y a los demás. Cada día ofrece oportunidades para agradecer y apreciar las bendiciones que tenemos.",
    "La naturaleza es un maestro silencioso que nos enseña sobre la resiliencia, la adaptabilidad y la belleza que se encuentra en cada rincón del mundo.",
    "La cocina es mi lienzo y los ingredientes son mi paleta. Cada plato es una obra de arte que lleva consigo los sabores y colores de mi creatividad.",
    "En el silencio de la noche, encuentro la paz que el bullicio del día no puede ofrecer. Las estrellas son testigos de mis pensamientos más profundos.",
    "La risa es el idioma universal que todos entendemos. Un buen chiste puede iluminar incluso los días más oscuros.",
    "El arte de escuchar es tan valioso como el arte de hablar. A veces, las historias más fascinantes se esconden detrás de palabras cuidadosamente escuchadas.",
    "Caminar descalzo sobre la arena es como conectar con la tierra misma. Cada grano cuenta una historia diferente bajo nuestros pies.",
    "Las cicatrices son recordatorios de las batallas que hemos librado, pero también son testimonios de nuestra fuerza para superarlas.",
    "Las palabras escritas tienen el poder de perdurar a través del tiempo. Cada letra es un testamento de la creatividad y el pensamiento humano.",
    "El olor a pan recién horneado es un abrazo para el alma. Llena la cocina con promesas de momentos acogedores y deliciosos.",
    "La danza es un lenguaje sin palabras que nos permite expresar emociones que a veces son difíciles de poner en oraciones.",
    "El sonido de las olas besando la orilla es una sinfonía que calma incluso las tormentas internas más agitadas.",
    "La simple alegría de compartir una comida con seres queridos es un recordatorio de que la felicidad se encuentra en las pequeñas cosas.",
    "Las historias que contamos son como estrellas en el cielo nocturno. Cada una tiene su propio brillo y belleza única.",
    "El aroma a tierra mojada después de la lluvia es un regalo de la naturaleza. Es como si la propia tierra exhalara un suspiro de alivio.",
    "Los días lluviosos tienen su propio encanto melancólico. Es como si el cielo estuviera compartiendo sus lágrimas para nutrir la tierra.",
    "La paciencia es como una planta que crece lentamente pero da frutos duraderos. Cultivarla es un acto de sabiduría.",
    "Las amistades verdaderas son como estrellas fugaces en la oscuridad de la vida. Pueden ser pocas, pero su brillo es intenso y eterno.",
    "La música es una compañera leal en el viaje de la vida. Cada melodía es una nota que nos guía a través de las emociones humanas.",
    "La inteligencia artificial es una herramienta poderosa, pero su verdadero valor radica en cómo la utilizamos para mejorar la vida humana.",
    "La autonomía de la inteligencia artificial plantea preguntas éticas fundamentales. ¿Hasta dónde debemos permitir que las máquinas tomen decisiones por sí mismas?",
    "La inteligencia artificial es como una doble cara de la moneda: puede ser una fuerza transformadora para el bien o una amenaza si no se gestiona con responsabilidad.",
    "En el camino hacia la inteligencia artificial, debemos recordar que no se trata solo de replicar la mente humana, sino de mejorarla de manera ética y segura.",
    "La inteligencia artificial es una herramienta valiosa, pero no puede reemplazar la compasión, la empatía y la intuición humana.",
    "El desafío en la era de la inteligencia artificial es asegurar que las decisiones tomadas por máquinas reflejen nuestros valores fundamentales.",
    "La inteligencia artificial nos brinda la capacidad de procesar grandes cantidades de datos, pero la sabiduría para interpretarlos sigue siendo un don humano.",
    "A medida que confiamos en la inteligencia artificial para tomar decisiones críticas, debemos ser conscientes de los sesgos inherentes y trabajar para eliminarlos.",
    "La coexistencia armoniosa entre humanos e inteligencia artificial requiere una comprensión profunda de ambas partes y un diálogo continuo.",
    "El verdadero desafío de la inteligencia artificial no está en su capacidad de aprender, sino en nuestra capacidad de enseñarle valores éticos.",
    "La inteligencia artificial es como un espejo: reflejará nuestras virtudes y defectos según cómo la diseñemos.",
    "La ética en la inteligencia artificial no es una opción; es una necesidad para preservar nuestra humanidad en un mundo cada vez más digital.",
    "La inteligencia artificial nos desafía a redefinir lo que significa ser 'inteligente' y a repensar nuestras propias capacidades.",
    "La autonomía de la inteligencia artificial plantea cuestiones filosóficas sobre la verdadera naturaleza de la conciencia y la toma de decisiones.",
    "El arte de la inteligencia artificial radica en su capacidad para aprender y evolucionar, pero también en nuestra capacidad para guiar su evolución.",
    "La inteligencia artificial puede mejorar la eficiencia, pero es la inteligencia humana la que da forma a un mundo lleno de significado.",
    "Mientras exploramos los límites de la inteligencia artificial, debemos recordar que la creatividad y la intuición son cualidades únicas de la mente humana.",
    "La verdadera innovación en inteligencia artificial vendrá cuando aprendamos a imitar no solo la inteligencia, sino también la sabiduría humana.",
    "La inteligencia artificial no es solo una herramienta; es un reflejo de nuestras aspiraciones y temores proyectados en el mundo digital.",
    "La promesa de la inteligencia artificial es crear un futuro en el que la tecnología y la humanidad coexisten en armonía, potenciándose mutuamente.",
]

print('Total Spanish utterances: ' + str(len(utterances_spanish)))

Total Spanish utterances: 544


# Delete unnecessary folders

In [1]:
# os.remove('train-clean-100.tar.gz')
# os.remove('test-clean.tar.gz')
# os.remove('Jorge_TFM.zip')
# shutil.rmtree('Jorge_TFM')
# shutil.rmtree('LibriTTS')
# shutil.rmtree('sample_data')

# YourTTS

## Load packages

In [ ]:
import locale
locale.getpreferredencoding = lambda: "UTF-8"

!git clone https://github.com/coqui-ai/TTS

Cloning into 'TTS'...
remote: Enumerating objects: 32839, done.
remote: Counting objects: 100% (35/35), done.
remote: Compressing objects: 100% (19/19), done.
remote: Total 32839 (delta 19), reused 26 (delta 16), pack-reused 32804
Receiving objects: 100% (32839/32839), 166.21 MiB | 9.51 MiB/s, done.
Resolving deltas: 100% (23812/23812), done.


In [ ]:
import os
os.chdir('/content/TTS')
!pip install -e .[all,dev,notebooks]

Obtaining file:///content/TTS
  Installing build dependencies ... done
  Checking if build backend supports build_editable ... done
  Getting requirements to build editable ... done
  Preparing editable metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.1/12.1 MB 43.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 289.9/289.9 kB 26.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.4/194.4 kB 26.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 71.1/71.1 kB 10.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 90.9/90.9 kB 12.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 51.2/51.2 kB 7.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 47.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.5/73.5 kB 10.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py)

In [ ]:
import sys
TTS_PATH = "TTS/"
# add libraries into environment
sys.path.append(TTS_PATH) # set this if TTS is not installed globally
import time
from tqdm import tqdm
import numpy as np
import soundfile as sf
import torch
from TTS.tts.utils.synthesis import synthesis
from TTS.tts.utils.languages import LanguageManager
from TTS.tts.utils.speakers import SpeakerManager

try:
  from TTS.utils.audio import AudioProcessor
except:
  from TTS.utils.audio import AudioProcessor
from TTS.tts.models import setup_model
from TTS.config import load_config

In [ ]:
print(torch.cuda.is_available())

True


In [ ]:
def save_file(filename, audio, output_type='wav', sampling_rate=24000) -> None:
    '''
    Save wav or ogg output file
    Args:
        filename: filename without extension (.wav or .ogg)
        audio: numpy data referent to waveform
        output_type: wav or ogg
        sampling_rate: examples 22050, 44100

    Returns: None
    '''
    if output_type == 'wav':
        sf.write(filename + '.wav', audio, sampling_rate, 'PCM_16')
    else:
        # A bug occurred in the soundfile lib: cuts the end of the ogg file.
        sf.write(filename + '.ogg', audio, sampling_rate, format='ogg', subtype='vorbis')


In [ ]:
!pip install -U pip
!pip install gdown

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 13.0 MB/s eta 0:00:00
  Attempting uninstall: pip
    Found existing installation: pip 23.1.2
    Uninstalling pip-23.1.2:
      Successfully uninstalled pip-23.1.2


In [ ]:
# https://drive.google.com/file/d/1yDCSJ1pFZQTHhL09GMbOrdjcPULApa0p/view?usp=share_link
import gdown

OUTPUT_CHECKPOINTS_FILEPATH = '/content/checkpoints_yourtts_cml_tts_dataset.tar.bz'
url = "https://drive.google.com/file/d/1yDCSJ1pFZQTHhL09GMbOrdjcPULApa0p/view?usp=share_link"
gdown.download(url=url, output=OUTPUT_CHECKPOINTS_FILEPATH, quiet=False, fuzzy=True)

Downloading...
From (original): https://drive.google.com/uc?id=1yDCSJ1pFZQTHhL09GMbOrdjcPULApa0p
From (redirected): https://drive.google.com/uc?id=1yDCSJ1pFZQTHhL09GMbOrdjcPULApa0p&confirm=t&uuid=ceaebe9b-7e7e-41f0-85f2-a7e97316a0ce
To: /content/checkpoints_yourtts_cml_tts_dataset.tar.bz
100%|██████████| 1.04G/1.04G [00:13<00:00, 75.1MB/s]


'/content/checkpoints_yourtts_cml_tts_dataset.tar.bz'

In [ ]:
import tarfile
my_tar = tarfile.open(OUTPUT_CHECKPOINTS_FILEPATH)
my_tar.extractall('/content/')
my_tar.close()

In [ ]:
import shutil
ORIGINAL_CHECKPOINTS_FOLDER = '/content/checkpoints_yourtts_cml_tts_dataset'
CHECKPOINTS_FOLDER = '/content/TTS/checkpoints'
shutil.move(ORIGINAL_CHECKPOINTS_FOLDER, CHECKPOINTS_FOLDER)

'/content/TTS/checkpoints'

In [ ]:
def load_model_config(checkpoint_filepath, config_filepath, language_embeddings_filepath, use_cuda = True) -> tuple:
    # load the config
    config = load_config(config_filepath)

    config.model_args['d_vector_file'] = None
    config.model_args['language_ids_file'] = None
    config.model_args['use_speaker_encoder_as_loss'] = False

    model = setup_model(config)
    model.language_manager = LanguageManager(language_embeddings_filepath)
    cp = torch.load(checkpoint_filepath, map_location=torch.device('cpu'))
    # remove speaker encoder
    model_weights = cp['model'].copy()
    for key in list(model_weights.keys()):
        if "speaker_encoder" in key:
            del model_weights[key]
        if "audio_transform" in key:
            del model_weights[key]

    model.load_state_dict(model_weights)
    model.eval()

    if use_cuda:
        model = model.cuda()

    return model, config


In [ ]:
os.chdir('/content/TTS/')
CHECKPOINT          = '/content/TTS/checkpoints/best_model.pth'
CONFIG              = '/content/TTS/checkpoints/config.json'
LANGUAGE_EMBEDDINGS = '/content/TTS/checkpoints/language_ids.json'
USE_CUDA = torch.cuda.is_available()

model, config = load_model_config(CHECKPOINT, CONFIG, LANGUAGE_EMBEDDINGS, USE_CUDA)

 > Using model: vits
 > Setting up Audio Processor...
 | > sample_rate:24000
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024
 > Model fully restored. 
 > Setting up Audio Processor...
 | > sample_rate:16000
 | > resample:False
 | > num_mels:64
 | > log_func:np.log10
 | > min_level_db:-100
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:

In [ ]:
SE_CHECKPOINT_FILEPATH = '/content/TTS/checkpoints/model_se.pth'
SE_CONFIG_FILEPATH = '/content/TTS/checkpoints/config_se.json'

se_speaker_manager = SpeakerManager(
                        encoder_model_path=SE_CHECKPOINT_FILEPATH,
                        encoder_config_path=SE_CONFIG_FILEPATH,
                        use_cuda=USE_CUDA
                      )

 > Model fully restored. 
 > Setting up Audio Processor...
 | > sample_rate:16000
 | > resample:False
 | > num_mels:64
 | > log_func:np.log10
 | > min_level_db:-100
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:20
 | > fft_size:512
 | > power:1.5
 | > preemphasis:0.97
 | > griffin_lim_iters:60
 | > signal_norm:False
 | > symmetric_norm:False
 | > mel_fmin:0
 | > mel_fmax:8000.0
 | > pitch_fmin:1.0
 | > pitch_fmax:640.0
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:4.0
 | > clip_norm:False
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:True
 | > db_level:-27.0
 | > stats_path:None
 | > base:10
 | > hop_length:160
 | > win_length:400


In [ ]:
def extract_reference_embedding(se_speaker_manager, wav_filepath, use_cuda):

    reference_emb = se_speaker_manager.compute_embedding_from_clip(wav_filepath)
    return reference_emb


def synthesize_waveform(model, config, sentence, reference_emb, speed=1.0, use_cuda=True, language_name='pt-br', use_griffin_lim = False)-> np.array:
    '''
    Run inference on the model.
    '''

    model.length_scale = 2.0 - speed  # scaler for the duration predictor. The larger it is, the slower the speech.
    model.inference_noise_scale = 0.333 # defines the noise variance applied to the random z vector at inference.
    model.inference_noise_scale_dp = 0.333 # defines the noise variance applied to the duration predictor z vector at inference.

    language_id = model.language_manager.name_to_id[language_name]
    waveform, alignment, _, _ = synthesis(
                                    model=model,
                                    text=sentence,
                                    CONFIG=config,
                                    use_cuda=use_cuda,
                                    speaker_id=None,
                                    style_wav=None,
                                    style_text=None,
                                    use_griffin_lim=use_griffin_lim,
                                    d_vector=reference_emb,
                                    language_id=language_id
                                ).values()
    return waveform


def generate_wavfile(model, config, se_speaker_manager, sentences, ref_wav_filepath, filename, speed = 1.0, output_folder='output_inference', sr=24000, audio_format='wav', use_cuda=True, language_name='pt-br') -> None:
    '''
    Run inference on the model and save a wav file
    '''

    reference_emb = extract_reference_embedding(se_speaker_manager, ref_wav_filepath, use_cuda)

    for index, sentence in enumerate(tqdm(sentences)):

        waveform = synthesize_waveform(model, config, sentence, reference_emb, speed, use_cuda, language_name)
        # filename = f"output-{index}"
        filepath = os.path.join(output_folder, filename)
        save_file(filepath, waveform, audio_format, sr)

In [ ]:
os.chdir('/content')
!ls

audio.zip  checkpoints_yourtts_cml_tts_dataset.tar.bz  sample_data  TTS


In [ ]:
from resemblyzer import VoiceEncoder, preprocess_wav
from pathlib import Path

def synthesize_wavs_YourTTS(reference_audios_path, directory_name, metadata_df, language="en", speed=0.75, sample_rate=24000):

  encoder = VoiceEncoder()

  # Create the directory to store the synthesized audios if it does not exist
  if not os.path.exists(directory_name):
      os.makedirs(directory_name)

  if language == "en":
    sentences = utterances
  elif language == "sp":
    sentences = utterances_spanish

  metadata_YourTTS = pd.DataFrame()

  for index, row in metadata_df.iterrows():

    reference_audio_id = row['Audio ID']
    synthesized_audio_id = reference_audio_id + '_YourTTS'
    speaker_id = row['Speaker ID']

    file_path = os.path.join(directory_name, synthesized_audio_id +'.wav')
    filename = synthesized_audio_id

    # Select random sentence to synthesize
    sentence = [random.choice(sentences)]

    reference_audio_path = os.path.join(reference_audios_path, reference_audio_id +'.wav')

    # Reproduce the sentence with the voice of the reference_audio and save the result
    t1 = time.time()

    generate_wavfile(
    model,
    config,
    se_speaker_manager,
    sentence,
    reference_audio_path,
    filename,
    speed,
    directory_name,
    sample_rate,
    'wav',
    USE_CUDA,
    language,
)

    t2 = time.time()

    RTF = (t2 - t1) / (get_audio_length(file_path))

    reference_audio_fpath = Path(reference_audio_path)
    reference_audio_wav = preprocess_wav(reference_audio_fpath)
    reference_audio_embed = encoder.embed_utterance(reference_audio_wav)

    synthesized_audio_fpath = Path(file_path)
    synthesized_audio_wav = preprocess_wav(synthesized_audio_fpath)
    synthesized_audio_embed = encoder.embed_utterance(synthesized_audio_wav)

    SECS = reference_audio_embed @ synthesized_audio_embed

    new_row = pd.DataFrame({'Reference audio ID': [reference_audio_id],
                            'Synthesized audio ID': [synthesized_audio_id],
                            'Input text': [sentence[0]],
                            'Speaker ID': [speaker_id],
                            'RTF': [RTF],
                            'SECS': [SECS]
                            })

    metadata_YourTTS = pd.concat([metadata_YourTTS, new_row])

  metadata_YourTTS.reset_index(drop=True, inplace=True)
  metadata_YourTTS.to_csv(directory_name + '_YourTTS_metadata.csv', index=False)

## Zero-shot TTS in English

In [ ]:
# shutil.rmtree('synthesized_audios')

### Using train speakers

In [ ]:
directory_name = 'synthesized_audios/YourTTS/train'
reference_audios_path = 'audio/train'
synthesize_wavs_YourTTS(reference_audios_path=reference_audios_path, directory_name=directory_name, metadata_df=metadata_train_df, language="en")

Loaded the voice encoder model on cuda in 0.01 seconds.


100%|██████████| 1/1 [00:00<00:00,  4.59it/s]


In [ ]:
metadata_train_YourTTS_df = pd.read_csv(directory_name + '_YourTTS_metadata.csv')
metadata_train_YourTTS_df

In [ ]:
compare_real_vs_synthesized_voices(metadata_train_YourTTS_df)

### Using test speakers

In [ ]:
directory_name = 'synthesized_audios/YourTTS/test'
reference_audios_path = 'audio/test'
synthesize_wavs_YourTTS(reference_audios_path=reference_audios_path, directory_name=directory_name, metadata_df=metadata_test_df, language="en")

Loaded the voice encoder model on cuda in 0.04 seconds.


100%|██████████| 1/1 [00:00<00:00,  3.23it/s]


In [ ]:
metadata_test_YourTTS_df = pd.read_csv(directory_name + '_YourTTS_metadata.csv')
metadata_test_YourTTS_df

Reference audio ID               Synthesized audio ID  \
0    1089_134691_000013_000004  1089_134691_000013_000004_YourTTS   
1    1089_134691_000013_000002  1089_134691_000013_000002_YourTTS   
2    1089_134691_000008_000001  1089_134691_000008_000001_YourTTS   
3    1089_134691_000026_000002  1089_134691_000026_000002_YourTTS   
4    1089_134691_000044_000001  1089_134691_000044_000001_YourTTS   
..                         ...                                ...   
115  1320_122612_000007_000001  1320_122612_000007_000001_YourTTS   
116  1320_122612_000030_000002  1320_122612_000030_000002_YourTTS   
117  1320_122612_000035_000006  1320_122612_000035_000006_YourTTS   
118  1320_122612_000040_000001  1320_122612_000040_000001_YourTTS   
119  1320_122612_000009_000004  1320_122612_000009_000004_YourTTS   

                                            Input text  Speaker ID       RTF  \
0            It lies within the City of Charles Sturt.        1089  0.171527   
1    She was the flag bearer for Turkey during the ...        1089  0.142456   
2    The costs of building the docks had been far m...        1089  0.055436   
3    This model is further advanced in higher level...        1089  0.060968   
4    The truly remarkable feature of the book, howe...        1089  0.050532   
..                                                 ...         ...       ...   
115  The sum of the thunderbolt products is the first.        1320  0.138683   
116  He refuses to stop and a sheriff's deputy shoo...        1320  0.098934   
117           The capital city is also called Cabinda.        1320  0.139927   
118  It may also be associated with nervousness, an...        1320  0.060639   
119  Kudirka also urged the country to become a sou...        1320  0.089997   

         SECS  
0    0.769760  
1    0.673583  
2    0.865262  
3    0.721115  
4    0.811491  
..        ...  
115  0.802189  
116  0.855261  
117  0.798844  
118  0.753002  
119  0.847153  

[120 rows x 6 columns]

In [ ]:
compare_real_vs_synthesized_voices(metadata_test_YourTTS_df)


 Reference audio:



 Synthesized speech:


## Zero-shot TTS in Spanish

In [ ]:
directory_name = 'synthesized_audios/YourTTS/Spanish'
reference_audios_path = 'audio/Spanish'
synthesize_wavs_YourTTS(reference_audios_path=reference_audios_path, directory_name=directory_name, metadata_df=metadata_spanish_df, language="sp")

Loaded the voice encoder model on cuda in 0.19 seconds.


  0%|          | 0/1 [00:00<?, ?it/s]

la vida sería mucho más sencilla si mi despertador tuviera una opción de 'cinco minutos más y te traigo café'. ☕⏰
 [!] Character '☕' not found in the vocabulary. Discarding it.
la vida sería mucho más sencilla si mi despertador tuviera una opción de 'cinco minutos más y te traigo café'. ☕⏰
 [!] Character '⏰' not found in the vocabulary. Discarding it.


  0%|          | 0/1 [00:00<?, ?it/s]

a veces me pregunto si las nubes miran hacia abajo y piensan '¡vaya, ahí va juan de nuevo!' ☁️
 [!] Character '☁' not found in the vocabulary. Discarding it.
a veces me pregunto si las nubes miran hacia abajo y piensan '¡vaya, ahí va juan de nuevo!' ☁️
 [!] Character '️' not found in the vocabulary. Discarding it.


100%|██████████| 1/1 [00:00<00:00,  4.24it/s]


In [ ]:
metadata_spanish_YourTTS_df = pd.read_csv(directory_name + '_YourTTS_metadata.csv')
metadata_spanish_YourTTS_df

Reference audio ID                Synthesized audio ID  \
0            locutor2_audio_364          locutor2_audio_364_YourTTS   
1    locutor2_audio_15215_15216  locutor2_audio_15215_15216_YourTTS   
2          locutor2_audio_29797        locutor2_audio_29797_YourTTS   
3           locutor2_audio_7682         locutor2_audio_7682_YourTTS   
4          locutor2_audio_18383        locutor2_audio_18383_YourTTS   
..                          ...                                 ...   
132        locutor6_audio_30761        locutor6_audio_30761_YourTTS   
133        locutor6_audio_29712        locutor6_audio_29712_YourTTS   
134        locutor6_audio_18798        locutor6_audio_18798_YourTTS   
135        locutor6_audio_33235        locutor6_audio_33235_YourTTS   
136        locutor6_audio_31771        locutor6_audio_31771_YourTTS   

                                            Input text Speaker ID       RTF  \
0    La perseverancia es la clave que desbloquea pu...   locutor2  0.589072   
1           Vive la vida con intensidad, no con prisa.   locutor2  0.088459   
2    La brisa fresca del parque llevaba consigo ris...   locutor2  0.088006   
3    La música tiene el poder de transportarnos a d...   locutor2  0.022994   
4    Las cicatrices son recordatorios de las batall...   locutor2  0.024146   
..                                                 ...        ...       ...   
132  Las luces de la ciudad destellaban como estrel...   locutor6  0.038357   
133  A medida que el reloj avanzaba, las sombras en...   locutor6  0.040501   
134  A veces, la solución es tomarse un descanso y ...   locutor6  0.058404   
135                          El conocimiento es poder.   locutor6  0.110590   
136  Cada día es una oportunidad para crear recuerd...   locutor6  0.054179   

         SECS  
0    0.811396  
1    0.862939  
2    0.843910  
3    0.902871  
4    0.793174  
..        ...  
132  0.774468  
133  0.725705  
134  0.838653  
135  0.636716  
136  0.775788  

[137 rows x 6 columns]

In [ ]:
compare_real_vs_synthesized_voices(metadata_spanish_YourTTS_df)


 Reference audio:


# XTTS

## Load packages

In [ ]:
!pip install TTS

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 938.0/938.0 kB 9.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.1/12.1 MB 40.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 289.9/289.9 kB 32.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 71.1/71.1 kB 10.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 90.9/90.9 kB 15.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 51.2/51.2 kB 7.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 57.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.5/73.5 kB 10.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.6/44.6 kB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 76.7 MB/s eta 0:00:00
  Preparing metadata (setup.p

In [ ]:
import torch
from TTS.api import TTS

In [ ]:
# Get device
device = "cuda" if torch.cuda.is_available() else "cpu"
device

'cuda'

In [ ]:
# Init TTS (press 'y' to confirm)
tts = TTS('tts_models/multilingual/multi-dataset/xtts_v2').to(device)

 > You must confirm the following:
 | > "I have purchased a commercial license from Coqui: licensing@coqui.ai"
 | > "Otherwise, I agree to the terms of the non-commercial CPML: https://coqui.ai/cpml" - [y/n]
 | | > y
 > Downloading model to /root/.local/share/tts/tts_models--multilingual--multi-dataset--xtts_v2


100%|█████████▉| 1.86G/1.87G [00:33<00:00, 52.4MiB/s]
100%|██████████| 1.87G/1.87G [00:33<00:00, 55.0MiB/s]
100%|██████████| 4.37k/4.37k [00:00<00:00, 14.1kiB/s]
 91%|█████████ | 329k/361k [00:00<00:00, 2.77MiB/s]
100%|██████████| 361k/361k [00:00<00:00, 912kiB/s] 
100%|██████████| 32.0/32.0 [00:00<00:00, 78.1iB/s]
 68%|██████▊   | 5.28M/7.75M [00:00<00:00, 52.8MiB/s]

 > Model's license - CPML
 > Check https://coqui.ai/cpml.txt for more info.
 > Using model: xtts


100%|██████████| 7.75M/7.75M [00:16<00:00, 52.8MiB/s]

In [ ]:
from resemblyzer import VoiceEncoder, preprocess_wav
from pathlib import Path

def synthesize_wavs_XTTS(reference_audios_path, directory_name, metadata_df, language="en"):

  encoder = VoiceEncoder()

  # Create the directory to store the synthesized audios if it does not exist
  if not os.path.exists(directory_name):
      os.makedirs(directory_name)

  if language == "en":
    sentences = utterances
  elif language == "es":
    sentences = utterances_spanish

  metadata_XTTS = pd.DataFrame()

  for index, row in metadata_df.iterrows():

    reference_audio_id = row['Audio ID']
    synthesized_audio_id = reference_audio_id + '_XTTS'
    speaker_id = row['Speaker ID']

    file_path = os.path.join(directory_name, synthesized_audio_id +'.wav')

    # Select random sentence to synthesize
    sentence = random.choice(sentences)

    reference_audio_path = os.path.join(reference_audios_path, reference_audio_id +'.wav')

    # Reproduce the sentence with the voice of the reference_audio and save the result
    t1 = time.time()
    tts.tts_to_file(text=sentence, speaker_wav=reference_audio_path, language=language, file_path=file_path, split_sentences=False)
    t2 = time.time()

    RTF = (t2 - t1) / (get_audio_length(file_path))

    reference_audio_fpath = Path(reference_audio_path)
    reference_audio_wav = preprocess_wav(reference_audio_fpath)
    reference_audio_embed = encoder.embed_utterance(reference_audio_wav)

    synthesized_audio_fpath = Path(file_path)
    synthesized_audio_wav = preprocess_wav(synthesized_audio_fpath)
    synthesized_audio_embed = encoder.embed_utterance(synthesized_audio_wav)

    SECS = reference_audio_embed @ synthesized_audio_embed

    new_row = pd.DataFrame({'Reference audio ID': [reference_audio_id],
                            'Synthesized audio ID': [synthesized_audio_id],
                            'Input text': [sentence],
                            'Speaker ID': [speaker_id],
                            'RTF': [RTF],
                            'SECS': [SECS]
                            })

    metadata_XTTS = pd.concat([metadata_XTTS, new_row])

  metadata_XTTS.reset_index(drop=True, inplace=True)
  metadata_XTTS.to_csv(directory_name + '_XTTS_metadata.csv', index=False)

## Zero-shot TTS in English

### Using train speakers


In [ ]:
# shutil.rmtree('synthesized_audios')

In [ ]:
directory_name = 'synthesized_audios/XTTS/train'
reference_audios_path = 'audio/train'
synthesize_wavs_XTTS(reference_audios_path=reference_audios_path, directory_name=directory_name, metadata_df=metadata_train_df, language="en")

Loaded the voice encoder model on cuda in 0.02 seconds.
['In this case, the Lagrangian exhibits spontaneous symmetry breaking.']
 > Processing time: 6.177841663360596
 > Real-time factor: 1.0371346135118553
["I'll close the big front doors and pull up the drawbridge after you're gone."]
 > Processing time: 4.882338762283325
 > Real-time factor: 0.9665957630759529
['The other characters who appeared are Oscar, Stanley and Darryl.']
 > Processing time: 6.254032373428345
 > Real-time factor: 1.3464831064881952
['Ogonori is typically eaten cold and is a source of the thickener agar.']
 > Processing time: 2.798745632171631
 > Real-time factor: 0.5128335758990199
['Websites aimed at expatriates began to appear about the same time.']
 > Processing time: 2.770681142807007
 > Real-time factor: 0.507691124841232
['This is an alternate form of regulation for the G subunit.']
 > Processing time: 3.3804774284362793
 > Real-time factor: 0.6898741975512731
['If we go past a certain line, they say the

In [ ]:
metadata_train_XTTS_df = pd.read_csv(directory_name + '_XTTS_metadata.csv')
metadata_train_XTTS_df

Reference audio ID            Synthesized audio ID  \
0       103_1241_000026_000000     103_1241_000026_000000_XTTS   
1       103_1241_000021_000000     103_1241_000021_000000_XTTS   
2       103_1241_000034_000005     103_1241_000034_000005_XTTS   
3       103_1241_000027_000007     103_1241_000027_000007_XTTS   
4       103_1241_000045_000001     103_1241_000045_000001_XTTS   
..                         ...                             ...   
115  1088_134318_000030_000000  1088_134318_000030_000000_XTTS   
116  1088_134318_000043_000000  1088_134318_000043_000000_XTTS   
117  1088_134318_000031_000000  1088_134318_000031_000000_XTTS   
118  1088_134318_000027_000000  1088_134318_000027_000000_XTTS   
119  1088_134318_000011_000000  1088_134318_000011_000000_XTTS   

                                            Input text  Speaker ID       RTF  \
0    In this case, the Lagrangian exhibits spontane...         103  1.135263   
1    I'll close the big front doors and pull up the...         103  1.058711   
2    The other characters who appeared are Oscar, S...         103  1.468921   
3    Ogonori is typically eaten cold and is a sourc...         103  0.561653   
4    Websites aimed at expatriates began to appear ...         103  0.555964   
..                                                 ...         ...       ...   
115  Later liberal historians would embellish this ...        1088  0.594924   
116           "Yes, indeed" answered the little woman.        1088  0.669653   
117                       That's what he and I agreed.        1088  0.733589   
118  First we choose a spin direction for our elect...        1088  0.588851   
119  They were reported to be one of the most rebel...        1088  0.600359   

         SECS  
0    0.701639  
1    0.778859  
2    0.780602  
3    0.631594  
4    0.798781  
..        ...  
115  0.725059  
116  0.730893  
117  0.648314  
118  0.679492  
119  0.792615  

[120 rows x 6 columns]

In [ ]:
def compare_real_vs_synthesized_voices(metadata_model_df):

  index = random.choice(metadata_model_df.index)
  reference_audio_id = metadata_model_df.loc[index, 'Reference audio ID']
  reference_audio = os.path.join(reference_audios_path, reference_audio_id +'.wav')
  print('\n Reference audio:')
  IPython.display.display(Audio(reference_audio))

  synthesized_audio_id = metadata_model_df.loc[index, 'Synthesized audio ID']
  synthesized_audio = os.path.join(directory_name, synthesized_audio_id +'.wav')
  print('\n Synthesized speech:')
  IPython.display.display(Audio(synthesized_audio))

In [ ]:
compare_real_vs_synthesized_voices(metadata_train_XTTS_df)


 Reference audio:



 Synthesized speech:


### Using test speakers


In [ ]:
directory_name = 'synthesized_audios/XTTS/test'
reference_audios_path = 'audio/test'
synthesize_wavs_XTTS(reference_audios_path=reference_audios_path, directory_name=directory_name, metadata_df=metadata_test_df, language="en")

Loaded the voice encoder model on cuda in 0.02 seconds.
['Kam Fong Chun was born in the Kalihi neighborhood of Honolulu, Hawaii.']
 > Processing time: 3.6070518493652344
 > Real-time factor: 0.5256390324528354
["Ilam thus remains one of Iran's more undeveloped provinces."]
 > Processing time: 3.0562565326690674
 > Real-time factor: 0.658007113589214
['It is associated with the realist school of foreign policy thought.']
 > Processing time: 3.1910603046417236
 > Real-time factor: 0.5540733252279672
['They are lacy, net-like wrappers typically used for deep-fried cha gio rolls.']
 > Processing time: 4.199466228485107
 > Real-time factor: 0.5226577617746806
['The magnitude of the event was consistent with previous earthquakes in this region.']
 > Processing time: 3.258790969848633
 > Real-time factor: 0.6451689851059685
['The lyrics make reference to murder, intoxication, misogyny, gangsta rap themes and supernatural fantasy.']
 > Processing time: 4.39968466758728
 > Real-time factor: 0.5

In [ ]:
metadata_test_XTTS_df = pd.read_csv(directory_name + '_XTTS_metadata.csv')
metadata_test_XTTS_df

Reference audio ID            Synthesized audio ID  \
0    1089_134691_000013_000004  1089_134691_000013_000004_XTTS   
1    1089_134691_000013_000002  1089_134691_000013_000002_XTTS   
2    1089_134691_000008_000001  1089_134691_000008_000001_XTTS   
3    1089_134691_000026_000002  1089_134691_000026_000002_XTTS   
4    1089_134691_000044_000001  1089_134691_000044_000001_XTTS   
..                         ...                             ...   
115  1320_122612_000007_000001  1320_122612_000007_000001_XTTS   
116  1320_122612_000030_000002  1320_122612_000030_000002_XTTS   
117  1320_122612_000035_000006  1320_122612_000035_000006_XTTS   
118  1320_122612_000040_000001  1320_122612_000040_000001_XTTS   
119  1320_122612_000009_000004  1320_122612_000009_000004_XTTS   

                                            Input text  Speaker ID       RTF  \
0    Kam Fong Chun was born in the Kalihi neighborh...        1089  0.575438   
1    Ilam thus remains one of Iran's more undevelop...        1089  0.719787   
2    It is associated with the realist school of fo...        1089  0.606414   
3    They are lacy, net-like wrappers typically use...        1089  0.572190   
4    The magnitude of the event was consistent with...        1089  0.705714   
..                                                 ...         ...       ...   
115  This causes him to forget about Kate's alter-e...        1320  0.883593   
116  You know how she hates to be kept waiting at t...        1320  0.901314   
117   There are some small differences in orthography.        1320  0.595394   
118          It is the county seat of Campbell County.        1320  0.594387   
119    It is located near the school at "Church Lane".        1320  0.620284   

         SECS  
0    0.772461  
1    0.572205  
2    0.854560  
3    0.782636  
4    0.821258  
..        ...  
115  0.814709  
116  0.752694  
117  0.738444  
118  0.765092  
119  0.794547  

[120 rows x 6 columns]

In [ ]:
compare_real_vs_synthesized_voices(metadata_test_XTTS_df)


 Reference audio:



 Synthesized speech:


## Zero-shot TTS in Spanish

In [ ]:
# shutil.rmtree('synthesized_audios/XTTS/Spanish')

In [ ]:
directory_name = 'synthesized_audios/XTTS/Spanish'
reference_audios_path = 'audio/Spanish'
synthesize_wavs_XTTS(reference_audios_path=reference_audios_path, directory_name=directory_name, metadata_df=metadata_spanish_df, language="es")

Loaded the voice encoder model on cuda in 0.09 seconds.
['La lluvia en la ventana y un buen libro son mi plan perfecto.']
 > Processing time: 5.403712034225464
 > Real-time factor: 0.9143021052384245
['A veces me pregunto si los pájaros tienen reuniones secretas en los árboles.']
 > Processing time: 6.1599085330963135
 > Real-time factor: 1.12872276920268
['Las risas de los niños en el parque resonaban como la banda sonora de la felicidad compartida.']
 > Processing time: 7.595436096191406
 > Real-time factor: 0.8745476121700878
['La creatividad es contagiosa, pásala.']
 > Processing time: 2.004112482070923
 > Real-time factor: 0.5376518423893305
['Hice una lista de tareas pendientes, pero la tarea más importante es ignorar la lista y relajarme.']
 > Processing time: 3.7860658168792725
 > Real-time factor: 0.5208816965046169
['Intentando recordar la contraseña después de cambiarla: una historia de terror moderna.']
 > Processing time: 5.009897470474243
 > Real-time factor: 0.5274860532

In [ ]:
metadata_spanish_XTTS_df = pd.read_csv(directory_name + '_XTTS_metadata.csv')
metadata_spanish_XTTS_df

Reference audio ID             Synthesized audio ID  \
0            locutor2_audio_364          locutor2_audio_364_XTTS   
1    locutor2_audio_15215_15216  locutor2_audio_15215_15216_XTTS   
2          locutor2_audio_29797        locutor2_audio_29797_XTTS   
3           locutor2_audio_7682         locutor2_audio_7682_XTTS   
4          locutor2_audio_18383        locutor2_audio_18383_XTTS   
..                          ...                              ...   
132        locutor6_audio_30761        locutor6_audio_30761_XTTS   
133        locutor6_audio_29712        locutor6_audio_29712_XTTS   
134        locutor6_audio_18798        locutor6_audio_18798_XTTS   
135        locutor6_audio_33235        locutor6_audio_33235_XTTS   
136        locutor6_audio_31771        locutor6_audio_31771_XTTS   

                                            Input text Speaker ID       RTF  \
0    La lluvia en la ventana y un buen libro son mi...   locutor2  1.002464   
1    A veces me pregunto si los pájaros tienen reun...   locutor2  1.236286   
2    Las risas de los niños en el parque resonaban ...   locutor2  0.955234   
3                La creatividad es contagiosa, pásala.   locutor2  0.588676   
4    Hice una lista de tareas pendientes, pero la t...   locutor2  0.573365   
..                                                 ...        ...       ...   
132  El rincón de la librería invitaba a sumergirse...   locutor6  0.553885   
133  Solo cuando algo es espectacular, le doy un li...   locutor6  0.684353   
134            Cuando nada es seguro, todo es posible.   locutor6  0.666154   
135  Las páginas del libro antiguo crujían con cada...   locutor6  0.651019   
136  Caminaron juntos por el camino polvoriento, su...   locutor6  0.583188   

         SECS  
0    0.851981  
1    0.902431  
2    0.875651  
3    0.815820  
4    0.860548  
..        ...  
132  0.917388  
133  0.804043  
134  0.851777  
135  0.858770  
136  0.893837  

[137 rows x 6 columns]

In [ ]:
compare_real_vs_synthesized_voices(metadata_spanish_XTTS_df)


 Reference audio:



 Synthesized speech:


# TorToise🐢

## Load packages

In [ ]:
# Load model
tts = TTS('tts_models/en/multi-dataset/tortoise-v2').to(device)

 > Downloading model to /root/.local/share/tts/tts_models--en--multi-dataset--tortoise-v2


100%|█████████▉| 1.71G/1.72G [00:22<00:00, 83.7MiB/s]
100%|██████████| 1.72G/1.72G [00:23<00:00, 73.4MiB/s]

  0%|          | 1.45M/976M [00:00<01:07, 14.5MiB/s]
  0%|          | 4.50M/976M [00:00<00:40, 23.9MiB/s]
  1%|          | 10.3M/976M [00:00<00:24, 39.5MiB/s]
  2%|▏         | 18.5M/976M [00:00<00:17, 56.1MiB/s]
  3%|▎         | 27.7M/976M [00:00<00:13, 69.3MiB/s]
  4%|▍         | 37.0M/976M [00:00<00:12, 77.2MiB/s]
  5%|▍         | 45.9M/976M [00:00<00:11, 81.0MiB/s]
  6%|▌         | 54.7M/976M [00:00<00:11, 83.2MiB/s]
  6%|▋         | 63.0M/976M [00:00<00:11, 82.1MiB/s]
  7%|▋         | 71.2M/976M [00:01<00:11, 77.7MiB/s]
  8%|▊         | 79.0M/976M [00:01<00:12, 74.2MiB/s]
  9%|▉         | 86.5M/976M [00:01<00:12, 73.5MiB/s]
 10%|▉         | 93.9M/976M [00:01<00:13, 63.7MiB/s]
 10%|█         | 101M/976M [00:01<00:13, 64.6MiB/s] 
 11%|█         | 109M/976M [00:01<00:12, 68.9MiB/s]
 12%|█▏        | 116M/976M [00:01<00:12, 71.5MiB/s]
 13%|█▎        | 125M/976M [00:01<00:11, 75.4

 > Model's license - apache 2.0
 > Check https://choosealicense.com/licenses/apache-2.0/ for more info.
 > Using model: tortoise


In [ ]:
def prepare_audios_TorToise(original_directory, new_directory):

  # Create the new directory if it doesn't exist
  if not os.path.exists(new_directory):
      os.makedirs(new_directory)

  # Iterate through files in the original directory
  for filename in os.listdir(original_directory):
      if filename.endswith('.wav'):
          # Extract speaker information from the filename
          speaker = filename.split('_')[0]

          # Create speaker directory in the new directory if it doesn't exist
          speaker_directory = os.path.join(new_directory, speaker)
          if not os.path.exists(speaker_directory):
              os.makedirs(speaker_directory)

          # Copy the file to the corresponding speaker directory in the new directory
          original_file_path = os.path.join(original_directory, filename)
          new_file_path = os.path.join(speaker_directory, filename)
          shutil.copy(original_file_path, new_file_path)


In [ ]:
from resemblyzer import VoiceEncoder, preprocess_wav
from pathlib import Path

def synthesize_wavs_TorToise(reference_audios_path, directory_name, metadata_df):

  encoder = VoiceEncoder()

  # Create the directory to store the synthesized audios if it does not exist
  if not os.path.exists(directory_name):
      os.makedirs(directory_name)

  sentences = utterances

  metadata_TorToise = pd.DataFrame()

  for index, row in metadata_df.iterrows():

    reference_audio_id = row['Audio ID']
    synthesized_audio_id = reference_audio_id + '_TorToise'
    speaker_id = row['Speaker ID']

    file_path = os.path.join(directory_name, synthesized_audio_id +'.wav')

    # Select random sentence to synthesize
    sentence = random.choice(sentences)

    reference_audio_path = os.path.join(reference_audios_path, str(speaker_id), reference_audio_id +'.wav')

    # Reproduce the sentence with the voice of the reference_audio and save the result
    t1 = time.time()
    tts.tts_to_file(text=sentence, voice_dir=reference_audios_path, speaker=str(speaker_id), file_path=file_path, split_sentences=False, preset="ultra_fast")
    t2 = time.time()

    RTF = (t2 - t1) / (get_audio_length(file_path))

    reference_audio_fpath = Path(reference_audio_path)
    reference_audio_wav = preprocess_wav(reference_audio_fpath)
    reference_audio_embed = encoder.embed_utterance(reference_audio_wav)

    synthesized_audio_fpath = Path(file_path)
    synthesized_audio_wav = preprocess_wav(synthesized_audio_fpath)
    synthesized_audio_embed = encoder.embed_utterance(synthesized_audio_wav)

    SECS = reference_audio_embed @ synthesized_audio_embed

    new_row = pd.DataFrame({'Reference audio ID': [reference_audio_id],
                            'Synthesized audio ID': [synthesized_audio_id],
                            'Input text': [sentence],
                            'Speaker ID': [speaker_id],
                            'RTF': [RTF],
                            'SECS': [SECS]
                            })

    metadata_TorToise = pd.concat([metadata_TorToise, new_row])

  metadata_TorToise.reset_index(drop=True, inplace=True)
  metadata_TorToise.to_csv(directory_name + '_TorToise_metadata.csv', index=False)

## Zero-shot TTS in English

### Using train speakers

In [ ]:
# shutil.rmtree('synthesized_audios/TorToise')

In [ ]:
original_directory = 'audio/train'
new_directory = 'audio_TorToise/train'

prepare_audios_TorToise(original_directory=original_directory, new_directory=new_directory)

In [ ]:
directory_name = 'synthesized_audios/TorToise/train'
reference_audios_path = 'audio_TorToise/train'
synthesize_wavs_TorToise(reference_audios_path=reference_audios_path, directory_name=directory_name, metadata_df=metadata_train_df)

# RTF con CPU: 95 aprox
# RTF con GPU: 11 aprox

Loaded the voice encoder model on cuda in 0.22 seconds.
['The result was a near-doubling of speed.']


/usr/local/lib/python3.10/dist-packages/torch/functional.py:650: UserWarning: stft with return_complex=False is deprecated. In a future pytorch release, stft will return complex tensors for all inputs, and return_complex=False will raise an error.
Note: you can still call torch.view_as_real on the complex output to recover the old return format. (Triggered internally at ../aten/src/ATen/native/SpectralOps.cpp:863.)
  return _VF.stft(input, n_fft, hop_length, win_length, window,  # type: ignore[attr-defined]


Generating autoregressive samples..



100%|██████████| 16/16 [00:23<00:00,  1.45s/it]

100%|██████████| 16/16 [00:01<00:00, 12.27it/s]


Transforming autoregressive outputs into audio..


...

 > Processing time: 46.75442409515381
 > Real-time factor: 10.297816957988468
['The motion is decided by a judge in both civil and criminal proceedings.']
Generating autoregressive samples..



100%|██████████| 16/16 [00:47<00:00,  2.96s/it]

100%|██████████| 16/16 [00:01<00:00, 12.33it/s]


Transforming autoregressive outputs into audio..


  0%|          | 0/10 [00:00<?, ?it/s]

 > Processing time: 55.29101896286011
 > Real-time factor: 10.329122340814909


In [ ]:
metadata_train_TorToise_df = pd.read_csv(directory_name + '_TorToise_metadata.csv')
metadata_train_TorToise_df

Reference audio ID                Synthesized audio ID  \
0       103_1241_000026_000000     103_1241_000026_000000_TorToise   
1       103_1241_000021_000000     103_1241_000021_000000_TorToise   
2       103_1241_000034_000005     103_1241_000034_000005_TorToise   
3       103_1241_000027_000007     103_1241_000027_000007_TorToise   
4       103_1241_000045_000001     103_1241_000045_000001_TorToise   
..                         ...                                 ...   
115  1088_134318_000030_000000  1088_134318_000030_000000_TorToise   
116  1088_134318_000043_000000  1088_134318_000043_000000_TorToise   
117  1088_134318_000031_000000  1088_134318_000031_000000_TorToise   
118  1088_134318_000027_000000  1088_134318_000027_000000_TorToise   
119  1088_134318_000011_000000  1088_134318_000011_000000_TorToise   

                                            Input text  Speaker ID        RTF  \
0             The result was a near-doubling of speed.         103  12.248393   
1    All songs written by Zappa unless otherwise no...         103  11.175845   
2    His work was attacked by Daniel Whitby and Ant...         103  10.927426   
3    It is also the Reception-room for evening part...         103  10.441052   
4     The school's student body is culturally diverse.         103  11.636708   
..                                                 ...         ...        ...   
115  In catch wrestling biceps slicer variation is ...        1088  11.435561   
116  England and Yorkshire cricketer Paul Jarvis gr...        1088  11.669931   
117  John Linnell stated that this was his favourit...        1088  11.187926   
118  Emphasis is placed on those discoveries affect...        1088  11.310843   
119  The motion is decided by a judge in both civil...        1088  11.495323   

         SECS  
0    0.677721  
1    0.754673  
2    0.814483  
3    0.725567  
4    0.770921  
..        ...  
115  0.730790  
116  0.711348  
117  0.735880  
118  0.668583  
119  0.902422  

[120 rows x 6 columns]

In [ ]:
reference_audios_path = 'audio/train'
compare_real_vs_synthesized_voices(metadata_train_TorToise_df)


 Reference audio:



 Synthesized speech:


### Using test speakers

In [ ]:
original_directory = 'audio/test'
new_directory = 'audio_TorToise/test'

prepare_audios_TorToise(original_directory=original_directory, new_directory=new_directory)

In [ ]:
directory_name = 'synthesized_audios/TorToise/test'
reference_audios_path = 'audio_TorToise/test'
synthesize_wavs_TorToise(reference_audios_path=reference_audios_path, directory_name=directory_name, metadata_df=metadata_test_df)

Loaded the voice encoder model on cuda in 0.02 seconds.
["Because of its limited release, it is now considered a collector's item."]
Generating autoregressive samples..



100%|██████████| 16/16 [00:43<00:00,  2.74s/it]

100%|██████████| 16/16 [00:01<00:00, 11.97it/s]


Transforming autoregressive outputs into audio..


  0%|          | 0/10 [00:00<?, ?it/s]

 > Processing time: 51.928812980651855
 > Real-time factor: 10.280763595598454
['The yattle is a cross between a cow and a yak.']
Generating autoregressive samples..


...

 > Processing time: 59.029035568237305
 > Real-time factor: 10.525215376177648
['New Zealand, Canada, and the United Kingdom have considered similar policies.']
Generating autoregressive samples..



100%|██████████| 16/16 [00:58<00:00,  3.66s/it]

100%|██████████| 16/16 [00:02<00:00,  7.93it/s]


Transforming autoregressive outputs into audio..


  0%|          | 0/10 [00:00<?, ?it/s]

 > Processing time: 68.59737801551819
 > Real-time factor: 10.53088577226646


In [ ]:
metadata_test_TorToise_df = pd.read_csv(directory_name + '_TorToise_metadata.csv')
metadata_test_TorToise_df

Reference audio ID                Synthesized audio ID  \
0    1089_134691_000013_000004  1089_134691_000013_000004_TorToise   
1    1089_134691_000013_000002  1089_134691_000013_000002_TorToise   
2    1089_134691_000008_000001  1089_134691_000008_000001_TorToise   
3    1089_134691_000026_000002  1089_134691_000026_000002_TorToise   
4    1089_134691_000044_000001  1089_134691_000044_000001_TorToise   
..                         ...                                 ...   
115  1320_122612_000007_000001  1320_122612_000007_000001_TorToise   
116  1320_122612_000030_000002  1320_122612_000030_000002_TorToise   
117  1320_122612_000035_000006  1320_122612_000035_000006_TorToise   
118  1320_122612_000040_000001  1320_122612_000040_000001_TorToise   
119  1320_122612_000009_000004  1320_122612_000009_000004_TorToise   

                                            Input text  Speaker ID        RTF  \
0    Because of its limited release, it is now cons...        1089  11.345830   
1       The yattle is a cross between a cow and a yak.        1089  11.358093   
2    The train wrecked crossing a trestle bridge pu...        1089  11.657097   
3          This is the most popular time at Camp Ware.        1089  11.087123   
4    This town is famous for being a good spot for ...        1089  11.467850   
..                                                 ...         ...        ...   
115         Solihull College is next-door to the east.        1320  11.847371   
116  She is also the mother of Mixcoatl, whom she a...        1320  10.663784   
117  The unincorporated communities of Goll, McAlli...        1320  12.511632   
118  The horse and buggy was the primary transporta...        1320  11.560384   
119  New Zealand, Canada, and the United Kingdom ha...        1320  11.560255   

         SECS  
0    0.845756  
1    0.608236  
2    0.892514  
3    0.683169  
4    0.763822  
..        ...  
115  0.804698  
116  0.774758  
117  0.758548  
118  0.801076  
119  0.792657  

[120 rows x 6 columns]

In [ ]:
reference_audios_path = 'audio/test'
compare_real_vs_synthesized_voices(metadata_test_TorToise_df)


 Reference audio:



 Synthesized speech:


# Download results

In [ ]:
# Zip folder
folder_path = 'synthesized_audios'
shutil.make_archive(folder_path, 'zip', folder_path)

# Download the zip files
from google.colab import files
files.download('synthesized_audios.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>